In [1]:
import torch.nn as nn 
import torch
from tqdm import tqdm
from torchlibrosa import Spectrogram,LogmelFilterBank
from torchlibrosa import SpecAugmentation
import torchaudio
import random
import librosa
import pandas as pd
import os
import numpy as np
from tqdm import tqdm
from sklearn.model_selection import train_test_split 
from sklearn.preprocessing import LabelEncoder
import torch.nn as nn
import torch
import IPython.display as ipd
import random
import warnings
from cProfile import label
from itertools import dropwhile
import torch.nn as nn 
import torch
from tqdm import tqdm
from torchlibrosa import Spectrogram,LogmelFilterBank
from torchlibrosa import SpecAugmentation
import torchaudio
import random
from torch.utils.tensorboard import SummaryWriter
writer=SummaryWriter("EventRecord")

class feedforward(nn.Module):
    def __init__(self,in_dim,out_dim,drop_rate=0.5,real_dim=10) -> None:
        super(feedforward,self).__init__()
        self.main=nn.Sequential(
            nn.LayerNorm(in_dim),
            nn.Linear(in_dim,out_dim),
            nn.GELU(),
            nn.Dropout(drop_rate),
            nn.Linear(out_dim,in_dim),
            nn.Dropout(drop_rate),
        )
        self.conv=nn.Conv1d(kernel_size=3,in_channels=real_dim,out_channels=real_dim,padding=1,stride=1,groups=real_dim)
        self.fuse=nn.Sequential(
            nn.Linear(3*in_dim,in_dim),
            nn.Dropout(drop_rate),
        )
    def forward(self,x):
        #print(x.shape)
        x=x.permute(0,2,1)
        proj=self.conv(x)
        #print(proj.shape,x.shape)
        pre=x
        x=self.main(x)+x
        return self.fuse(torch.concat([x,pre,proj],dim=2)).permute(0,2,1)
class DenseMLPBlock(nn.Module):
    def __init__(self,in_dim,out_dim,drop_rate=0.5,layer_scale_init=1e-6,lenth=10,alpha=2) -> None:
        super(DenseMLPBlock,self).__init__()
        self.spa=feedforward(lenth,lenth*alpha,drop_rate=drop_rate,real_dim=in_dim)
        self.li=nn.Sequential(
            nn.LayerNorm(in_dim),
            nn.Linear(in_dim,out_dim),
            nn.GELU(),
            nn.Dropout(drop_rate),)
        self.gamma=nn.Parameter(layer_scale_init*torch.ones(out_dim),requires_grad=True)
        self.gamma_fi=nn.Parameter(layer_scale_init*torch.ones(in_dim))
        self.large=nn.Sequential(
            nn.Linear(in_dim,out_dim,bias=False),
            nn.Dropout(drop_rate),
        )
    def forward(self,x):
        #print(x.shape)
        x=self.gamma_fi*(self.spa(x))+x
        return self.gamma*(self.li(x)+self.large(x))
class PIPMN(nn.Module):
    def __init__(self,in_dim=50,num_classes=10,drop_rate=0.5,layer_dim_coef=[4,8],init_layer_scale=1e-6,num_heads=4,process_lenth=1):
        super(PIPMN,self).__init__()
        self.first_in=nn.ModuleList()
        self.first_out=nn.ModuleList()
        self.layer_parameter_in=nn.ParameterList()
        self.layer_parameter_out=nn.ParameterList()
        self.coef=layer_dim_coef.copy()
        self.in_dim=in_dim
        self.small=nn.AdaptiveAvgPool1d(process_lenth)
        final_lenth=process_lenth
        for i in range(len(layer_dim_coef)):
            layer_dim_coef[i]*=in_dim
            print(layer_dim_coef[i])
           
        for i in range(len(layer_dim_coef)):
            if(i==0):
                self.first_in.append(DenseMLPBlock(in_dim,layer_dim_coef[i],drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_in.append(nn.Parameter(init_layer_scale*torch.ones(in_dim)))
            else:
                self.first_in.append(DenseMLPBlock(layer_dim_coef[i-1],layer_dim_coef[i],drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_in.append(nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[i-1])))
        # self.middle=DenseMLPBlock(layer_dim_coef[-1],layer_dim_coef[-1],drop_rate)
        # self.middle_layer=nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[-1]))
        # self.atten=nn.MultiheadAttention(embed_dim=layer_dim_coef[-1],num_heads=num_heads,dropout=0.8,batch_first=True)
        for i in range(len(layer_dim_coef)-1,-1,-1):
            if(i==0):
                self.first_out.append(DenseMLPBlock(layer_dim_coef[i],in_dim,drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_out.append(nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[i])))
            else:
                self.first_out.append(DenseMLPBlock(layer_dim_coef[i],layer_dim_coef[i-1],drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_out.append(nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[i])))
        self.final=nn.Sequential(
            nn.LayerNorm(in_dim),
            nn.Linear(in_dim,num_classes),
            nn.Softmax()
            )
        self.apply(self._init_weight)
    def _init_weight(self,m):
        if isinstance(m,(nn.Conv1d,nn.Linear)):
            nn.init.trunc_normal_(m.weight,std=0.02)
    def forward(self,x):
        # if(len(x.shape)==3):
        #     x=x.mean(2)#dim
        #x=x.permute(0,2,1)

        x=self.small(x.permute(0,2,1).float()).permute(0,2,1)
        
        #zero=zero.permute(0,2,1)
        #print(zero.shape,self.coef[-1])
        #zero=torch.repeat_interleave(zero,self.coef[-1],2)
        #print(zero.shape,x.shape)
        in_=[]
        in_.append(x*self.layer_parameter_in[0])
        for i in range(len(self.first_in)):
            x=self.first_in[i](x)
            #print(x.shape)
            # if(i!= len(self.layer_parameter_in)-1):
            #     x=x*self.layer_parameter_in[i+1]
            in_.append(x)
        #print(x.shape)
        #x=x.permute(0,2,1)

        # x,_=self.atten(x,zero,x)
        # x=x*self.middle_layer+in_[-1]
        #print(x.shape)
        
        #x=x.permute(0,2,1)
        in_.pop()
        in_.reverse()
        for i in range(len(self.first_out)):
            #x=self.first_out[i](x)
            x=self.first_out[i](x)+in_[i]
        return self.final(x.mean(1))

In [4]:
#0.955(42)  0.954(21)  0.956(35) 0.952(10) 
random_state=15
import librosa
import pandas as pd
import os
import numpy as np
from tqdm import tqdm
from sklearn.model_selection import train_test_split 
from sklearn.preprocessing import LabelEncoder
import torch.nn as nn
import torch
import IPython.display as ipd
import random
import warnings
from cProfile import label
from itertools import dropwhile
import torch.nn as nn 
import torch
from tqdm import tqdm
from torchlibrosa import Spectrogram,LogmelFilterBank
from torchlibrosa import SpecAugmentation
import torchaudio
import random
from torch.utils.tensorboard import SummaryWriter
#Audio Single
from torch.utils.tensorboard import SummaryWriter
from torch.utils.data import DataLoader,Dataset
model=PIPMN(in_dim=100,num_classes=10,layer_dim_coef=[4,8],drop_rate=0.5,process_lenth=5).cuda()
from torch.utils.data import DataLoader,Dataset
class UB8(Dataset):
    def __init__(self,path="D:/Living_and_Study_In_University/Dataset/UrbanSound8K",random_state=42,train=True):
        super(UB8,self).__init__()
        self.path=path
        self.random_state=random_state
        self.train=train
        self.df = pd.read_csv(self.path+'/metadata/UrbanSound8K.csv')
        extracted = []
        for index_num,row in tqdm(self.df.iterrows()):
            warnings.filterwarnings('ignore')
            file_name = os.path.join(os.path.abspath(self.path),'fold'+str(row["fold"])+'/',str(row['slice_file_name'])) 
            final_class_labels = row['class']   
            feature=np.load(os.path.abspath(self.path)+"/Numpy_4_gfcc_bfcc_mfcc_lfcc_ngcc/"+'fold'+str(row["fold"])+'/'+str(row['slice_file_name']).split('.')[0]+'.npy')
            extracted.append([feature,final_class_labels])
        ext_df = pd.DataFrame(extracted,columns=['feature','class'])
        x_all = np.array(ext_df[['feature']].to_numpy())
        x=[]
        for i in x_all:
            #print(i[0].shape)
            x.append(i[0])
        y = np.array(ext_df['class'].tolist())
        le = LabelEncoder()
        y = le.fit_transform(y)
        y_all=np.eye(10)[y]
        x_train, x_test, y_train, y_test = train_test_split(np.array(x), y_all, test_size=0.2, random_state = self.random_state)
        if self.train:
            self.x=torch.tensor(x_train).float()
            self.y=y_train
        else:
            self.x=torch.tensor(x_test).float()
            self.y=y_test
    def __getitem__(self,index):
        return self.x[index],self.y[index]
    def __len__(self):
        return len(self.x)
train_dataset=UB8(train=True,random_state=random_state)
test_dataset=UB8(train=False,random_state=random_state)
batch_size=128
loss_function=nn.CrossEntropyLoss(label_smoothing=0.1)
optimizer=torch.optim.AdamW(model.parameters(),lr=0.001)
model.cuda()
model.train()
epoches=3500
wrtier=SummaryWriter("Classification")
count=0
for epoch in range(epoches):
    all_correct=0
    all_cnt=0
    model.train()
    train_loader=DataLoader(train_dataset,batch_size=batch_size,shuffle=True)
    test_loader=DataLoader(test_dataset,batch_size=batch_size,shuffle=True)
    for index,(data,label) in enumerate(train_loader):
        if(count<=2):
            print(data.shape)
            count+=1
        data=data.cuda()
        label=label.cuda()
        optimizer.zero_grad()
        output=model(data)
        all_cnt+=data.shape[0]
        loss=loss_function(output,label)
        all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
        loss.backward()
        optimizer.step()
        #wrtier.add_scalar("Train_loss_Single_Modal",loss,index+epoch*len(train_loader))
        #wrtier.add_scalar("Train_accuracy_Single_Modal",all_correct/(all_cnt),index+epoch*len(train_loader))

    print("Epoch: ",epoch,"Train Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)
        
    model.eval()
    with torch.no_grad():
        all_correct=0
        all_cnt=0
        for index,(data,label) in enumerate(test_loader):
            if(count<=2):
                print(data.shape)
                count+=1
            data=data.cuda()
            label=label.cuda()
            output=model(data)
            all_cnt+=data.shape[0]
            all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
            loss=loss_function(output,label)
            #wrtier.add_scalar("Test_accuracy_Single_Modal",all_correct/(all_cnt),epoch)
            #wrtier.add_scalar("Test_loss_Single_Modal",loss,epoch)
        print("Epoch: ",epoch,"Test Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)

400
800


8732it [00:04, 2051.90it/s]
8732it [00:03, 2189.19it/s]


torch.Size([128, 399, 100])
torch.Size([128, 399, 100])
torch.Size([128, 399, 100])
Epoch:  0 Train Accuracy:  tensor(0.3510, device='cuda:0')  Loss:  tensor(2.0824, device='cuda:0', dtype=torch.float64, grad_fn=<DivBackward1>)
Epoch:  0 Test Accuracy:  tensor(0.4293, device='cuda:0')  Loss:  tensor(2.1212, device='cuda:0', dtype=torch.float64)
Epoch:  1 Train Accuracy:  tensor(0.5016, device='cuda:0')  Loss:  tensor(2.0203, device='cuda:0', dtype=torch.float64, grad_fn=<DivBackward1>)
Epoch:  1 Test Accuracy:  tensor(0.5323, device='cuda:0')  Loss:  tensor(2.0288, device='cuda:0', dtype=torch.float64)
Epoch:  2 Train Accuracy:  tensor(0.5510, device='cuda:0')  Loss:  tensor(1.9385, device='cuda:0', dtype=torch.float64, grad_fn=<DivBackward1>)
Epoch:  2 Test Accuracy:  tensor(0.5369, device='cuda:0')  Loss:  tensor(1.9354, device='cuda:0', dtype=torch.float64)
Epoch:  3 Train Accuracy:  tensor(0.5717, device='cuda:0')  Loss:  tensor(1.8661, device='cuda:0', dtype=torch.float64, grad_fn

In [18]:
#Without 1  0.951
import torch.nn as nn 
import torch
from tqdm import tqdm
from torchlibrosa import Spectrogram,LogmelFilterBank
from torchlibrosa import SpecAugmentation
import torchaudio
import random
import librosa
import pandas as pd
import os
import numpy as np
from tqdm import tqdm
from sklearn.model_selection import train_test_split 
from sklearn.preprocessing import LabelEncoder
import torch.nn as nn
import torch
import IPython.display as ipd
import random
import warnings
from cProfile import label
from itertools import dropwhile
import torch.nn as nn 
import torch
from tqdm import tqdm
from torchlibrosa import Spectrogram,LogmelFilterBank
from torchlibrosa import SpecAugmentation
import torchaudio
import random
from torch.utils.tensorboard import SummaryWriter
writer=SummaryWriter("EventRecord")

class feedforward(nn.Module):
    def __init__(self,in_dim,out_dim,drop_rate=0.5,real_dim=10) -> None:
        super(feedforward,self).__init__()
        self.main=nn.Sequential(
            nn.LayerNorm(in_dim),
            nn.Linear(in_dim,out_dim),
            nn.GELU(),
            nn.Dropout(drop_rate),
            nn.Linear(out_dim,in_dim),
            nn.Dropout(drop_rate),
        )
        self.conv=nn.Conv1d(kernel_size=3,in_channels=real_dim,out_channels=real_dim,padding=1,stride=1,groups=real_dim)
        self.fuse=nn.Sequential(
            nn.Linear(3*in_dim,in_dim),
            nn.Dropout(drop_rate),
        )
    def forward(self,x):
        #print(x.shape)
        x=x.permute(0,2,1)
        proj=self.conv(x)
        #print(proj.shape,x.shape)
        pre=x
        x=self.main(x)+x
        return self.fuse(torch.concat([x,pre,proj],dim=2)).permute(0,2,1)
class DenseMLPBlock(nn.Module):
    def __init__(self,in_dim,out_dim,drop_rate=0.5,layer_scale_init=1e-6,lenth=10,alpha=2) -> None:
        super(DenseMLPBlock,self).__init__()
        self.spa=feedforward(lenth,lenth*alpha,drop_rate=drop_rate,real_dim=in_dim)
        self.li=nn.Sequential(
            nn.LayerNorm(in_dim),
            nn.Linear(in_dim,out_dim),
            nn.GELU(),
            nn.Dropout(drop_rate),)
        self.gamma=nn.Parameter(layer_scale_init*torch.ones(out_dim),requires_grad=True)
        self.gamma_fi=nn.Parameter(layer_scale_init*torch.ones(in_dim))
        self.large=nn.Sequential(
            nn.Linear(in_dim,out_dim,bias=False),
            nn.Dropout(drop_rate),
        )
    def forward(self,x):
        #print(x.shape)
        x=self.gamma_fi*(self.spa(x))+x
        return self.gamma*(self.li(x)+self.large(x))
class PIPMN(nn.Module):
    def __init__(self,in_dim=50,num_classes=10,drop_rate=0.5,layer_dim_coef=[4,8],init_layer_scale=1e-6,num_heads=4,process_lenth=1):
        super(PIPMN,self).__init__()
        self.first_in=nn.ModuleList()
        self.first_out=nn.ModuleList()
        self.layer_parameter_in=nn.ParameterList()
        self.layer_parameter_out=nn.ParameterList()
        self.coef=layer_dim_coef.copy()
        self.in_dim=in_dim
        self.small=nn.AdaptiveAvgPool1d(process_lenth)
        final_lenth=process_lenth
        for i in range(len(layer_dim_coef)):
            layer_dim_coef[i]*=in_dim
            print(layer_dim_coef[i])
           
        for i in range(len(layer_dim_coef)):
            if(i==0):
                self.first_in.append(DenseMLPBlock(in_dim,layer_dim_coef[i],drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_in.append(nn.Parameter(init_layer_scale*torch.ones(in_dim)))
            else:
                self.first_in.append(DenseMLPBlock(layer_dim_coef[i-1],layer_dim_coef[i],drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_in.append(nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[i-1])))
        # self.middle=DenseMLPBlock(layer_dim_coef[-1],layer_dim_coef[-1],drop_rate)
        # self.middle_layer=nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[-1]))
        # self.atten=nn.MultiheadAttention(embed_dim=layer_dim_coef[-1],num_heads=num_heads,dropout=0.8,batch_first=True)
        for i in range(len(layer_dim_coef)-1,-1,-1):
            if(i==0):
                self.first_out.append(DenseMLPBlock(layer_dim_coef[i],in_dim,drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_out.append(nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[i])))
            else:
                self.first_out.append(DenseMLPBlock(layer_dim_coef[i],layer_dim_coef[i-1],drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_out.append(nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[i])))
        self.final=nn.Sequential(
            nn.LayerNorm(in_dim),
            nn.Linear(in_dim,num_classes),
            nn.Softmax()
            )
        self.apply(self._init_weight)
    def _init_weight(self,m):
        if isinstance(m,(nn.Conv1d,nn.Linear)):
            nn.init.trunc_normal_(m.weight,std=0.02)
    def forward(self,x):
        # if(len(x.shape)==3):
        #     x=x.mean(2)#dim
        #x=x.permute(0,2,1)

        x=self.small(x.permute(0,2,1).float()).permute(0,2,1)
        
        #zero=zero.permute(0,2,1)
        #print(zero.shape,self.coef[-1])
        #zero=torch.repeat_interleave(zero,self.coef[-1],2)
        #print(zero.shape,x.shape)
        in_=[]
        in_.append(x*self.layer_parameter_in[0])
        for i in range(len(self.first_in)):
            x=self.first_in[i](x)
            #print(x.shape)
            # if(i!= len(self.layer_parameter_in)-1):
            #     x=x*self.layer_parameter_in[i+1]
            in_.append(x)
        #print(x.shape)
        #x=x.permute(0,2,1)

        # x,_=self.atten(x,zero,x)
        # x=x*self.middle_layer+in_[-1]
        #print(x.shape)
        
        #x=x.permute(0,2,1)
        in_.pop()
        in_.reverse()
        for i in range(len(self.first_out)):
            #x=self.first_out[i](x)
            x=self.first_out[i](x)
        return self.final(x.mean(1))
import librosa
import pandas as pd
import os
import numpy as np
from tqdm import tqdm
from sklearn.model_selection import train_test_split 
from sklearn.preprocessing import LabelEncoder
import torch.nn as nn
import torch
import IPython.display as ipd
import random
import warnings
from cProfile import label
from itertools import dropwhile
import torch.nn as nn 
import torch
from tqdm import tqdm
from torchlibrosa import Spectrogram,LogmelFilterBank
from torchlibrosa import SpecAugmentation
import torchaudio
import random
from torch.utils.tensorboard import SummaryWriter
#Audio Single
from torch.utils.tensorboard import SummaryWriter
from torch.utils.data import DataLoader,Dataset
model=PIPMN(in_dim=100,num_classes=10,layer_dim_coef=[4,8],drop_rate=0.5,process_lenth=5).cuda()
from torch.utils.data import DataLoader,Dataset
class UB8(Dataset):
    def __init__(self,path="D:/Living_and_Study_In_University/Dataset/UrbanSound8K",random_state=42,train=True):
        super(UB8,self).__init__()
        self.path=path
        self.random_state=random_state
        self.train=train
        self.df = pd.read_csv(self.path+'/metadata/UrbanSound8K.csv')
        extracted = []
        for index_num,row in tqdm(self.df.iterrows()):
            warnings.filterwarnings('ignore')
            file_name = os.path.join(os.path.abspath(self.path),'fold'+str(row["fold"])+'/',str(row['slice_file_name'])) 
            final_class_labels = row['class']   
            feature=np.load(os.path.abspath(self.path)+"/Numpy_4_gfcc_bfcc_mfcc_lfcc_ngcc/"+'fold'+str(row["fold"])+'/'+str(row['slice_file_name']).split('.')[0]+'.npy')
            extracted.append([feature,final_class_labels])
        ext_df = pd.DataFrame(extracted,columns=['feature','class'])
        x_all = np.array(ext_df[['feature']].to_numpy())
        x=[]
        for i in x_all:
            #print(i[0].shape)
            x.append(i[0])
        y = np.array(ext_df['class'].tolist())
        le = LabelEncoder()
        y = le.fit_transform(y)
        y_all=np.eye(10)[y]
        x_train, x_test, y_train, y_test = train_test_split(np.array(x), y_all, test_size=0.2, random_state = self.random_state)
        if self.train:
            self.x=torch.tensor(x_train).float()
            self.y=y_train
        else:
            self.x=torch.tensor(x_test).float()
            self.y=y_test
    def __getitem__(self,index):
        return self.x[index],self.y[index]
    def __len__(self):
        return len(self.x)
train_dataset=UB8(train=True)
test_dataset=UB8(train=False)
batch_size=len(train_dataset)
train_loader=DataLoader(train_dataset,batch_size=batch_size,shuffle=True)
test_loader=DataLoader(test_dataset,batch_size=batch_size,shuffle=True)
loss_function=nn.CrossEntropyLoss(label_smoothing=0.1)
optimizer=torch.optim.AdamW(model.parameters(),lr=0.001)
model.cuda()
model.train()
epoches=3500
wrtier=SummaryWriter("Classification")
count=0
for epoch in range(epoches):
    all_correct=0
    all_cnt=0
    model.train()
    for index,(data,label) in enumerate(train_loader):
        if(count<=2):
            print(data.shape)
            count+=1
        data=data.cuda()
        label=label.cuda()
        optimizer.zero_grad()
        output=model(data)
        all_cnt+=data.shape[0]
        loss=loss_function(output,label)
        all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
        loss.backward()
        optimizer.step()
        #wrtier.add_scalar("Train_loss_Single_Modal",loss,index+epoch*len(train_loader))
        #wrtier.add_scalar("Train_accuracy_Single_Modal",all_correct/(all_cnt),index+epoch*len(train_loader))

    print("Epoch: ",epoch,"Train Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)
        
    model.eval()
    with torch.no_grad():
        all_correct=0
        all_cnt=0
        for index,(data,label) in enumerate(test_loader):
            if(count<=2):
                print(data.shape)
                count+=1
            data=data.cuda()
            label=label.cuda()
            output=model(data)
            all_cnt+=data.shape[0]
            all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
            loss=loss_function(output,label)
            #wrtier.add_scalar("Test_accuracy_Single_Modal",all_correct/(all_cnt),epoch)
            #wrtier.add_scalar("Test_loss_Single_Modal",loss,epoch)
        print("Epoch: ",epoch,"Test Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)

400
800


8732it [00:05, 1508.11it/s]
8732it [00:04, 1807.54it/s]


torch.Size([6985, 399, 100])
Epoch:  0 Train Accuracy:  tensor(0.1102, device='cuda:0')  Loss:  tensor(2.3036, device='cuda:0', dtype=torch.float64, grad_fn=<DivBackward1>)
torch.Size([1747, 399, 100])
Epoch:  0 Test Accuracy:  tensor(0.1317, device='cuda:0')  Loss:  tensor(2.3033, device='cuda:0', dtype=torch.float64)
torch.Size([6985, 399, 100])
Epoch:  1 Train Accuracy:  tensor(0.1102, device='cuda:0')  Loss:  tensor(2.3035, device='cuda:0', dtype=torch.float64, grad_fn=<DivBackward1>)
Epoch:  1 Test Accuracy:  tensor(0.1317, device='cuda:0')  Loss:  tensor(2.3032, device='cuda:0', dtype=torch.float64)
Epoch:  2 Train Accuracy:  tensor(0.1102, device='cuda:0')  Loss:  tensor(2.3034, device='cuda:0', dtype=torch.float64, grad_fn=<DivBackward1>)
Epoch:  2 Test Accuracy:  tensor(0.1317, device='cuda:0')  Loss:  tensor(2.3029, device='cuda:0', dtype=torch.float64)
Epoch:  3 Train Accuracy:  tensor(0.1102, device='cuda:0')  Loss:  tensor(2.3031, device='cuda:0', dtype=torch.float64, grad

In [20]:
#without 2  0.952
import torch.nn as nn 
import torch
from tqdm import tqdm
from torchlibrosa import Spectrogram,LogmelFilterBank
from torchlibrosa import SpecAugmentation
import torchaudio
import random
import librosa
import pandas as pd
import os
import numpy as np
from tqdm import tqdm
from sklearn.model_selection import train_test_split 
from sklearn.preprocessing import LabelEncoder
import torch.nn as nn
import torch
import IPython.display as ipd
import random
import warnings
from cProfile import label
from itertools import dropwhile
import torch.nn as nn 
import torch
from tqdm import tqdm
from torchlibrosa import Spectrogram,LogmelFilterBank
from torchlibrosa import SpecAugmentation
import torchaudio
import random
from torch.utils.tensorboard import SummaryWriter
writer=SummaryWriter("EventRecord")

class feedforward(nn.Module):
    def __init__(self,in_dim,out_dim,drop_rate=0.5,real_dim=10) -> None:
        super(feedforward,self).__init__()
        self.main=nn.Sequential(
            nn.LayerNorm(in_dim),
            nn.Linear(in_dim,out_dim),
            nn.GELU(),
            nn.Dropout(drop_rate),
            nn.Linear(out_dim,in_dim),
            nn.Dropout(drop_rate),
        )
        #self.conv=nn.Conv1d(kernel_size=3,in_channels=real_dim,out_channels=real_dim,padding=1,stride=1,groups=real_dim)
        self.fuse=nn.Sequential(
            nn.Linear(2*in_dim,in_dim),
            nn.Dropout(drop_rate),
        )
    def forward(self,x):
        #print(x.shape)
        x=x.permute(0,2,1)
        #proj=self.conv(x)
        #print(proj.shape,x.shape)
        pre=x
        x=self.main(x)+x
        return self.fuse(torch.concat([x,pre],dim=2)).permute(0,2,1)
class DenseMLPBlock(nn.Module):
    def __init__(self,in_dim,out_dim,drop_rate=0.5,layer_scale_init=1e-6,lenth=10,alpha=2) -> None:
        super(DenseMLPBlock,self).__init__()
        self.spa=feedforward(lenth,lenth*alpha,drop_rate=drop_rate,real_dim=in_dim)
        self.li=nn.Sequential(
            nn.LayerNorm(in_dim),
            nn.Linear(in_dim,out_dim),
            nn.GELU(),
            nn.Dropout(drop_rate),)
        self.gamma=nn.Parameter(layer_scale_init*torch.ones(out_dim),requires_grad=True)
        self.gamma_fi=nn.Parameter(layer_scale_init*torch.ones(in_dim))
        self.large=nn.Sequential(
            nn.Linear(in_dim,out_dim,bias=False),
            nn.Dropout(drop_rate),
        )
    def forward(self,x):
        #print(x.shape)
        x=self.gamma_fi*(self.spa(x))+x
        return self.gamma*(self.li(x))
class PIPMN(nn.Module):
    def __init__(self,in_dim=50,num_classes=10,drop_rate=0.5,layer_dim_coef=[4,8],init_layer_scale=1e-6,num_heads=4,process_lenth=1):
        super(PIPMN,self).__init__()
        self.first_in=nn.ModuleList()
        self.first_out=nn.ModuleList()
        self.layer_parameter_in=nn.ParameterList()
        self.layer_parameter_out=nn.ParameterList()
        self.coef=layer_dim_coef.copy()
        self.in_dim=in_dim
        self.small=nn.AdaptiveAvgPool1d(process_lenth)
        final_lenth=process_lenth
        for i in range(len(layer_dim_coef)):
            layer_dim_coef[i]*=in_dim
            print(layer_dim_coef[i])
           
        for i in range(len(layer_dim_coef)):
            if(i==0):
                self.first_in.append(DenseMLPBlock(in_dim,layer_dim_coef[i],drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_in.append(nn.Parameter(init_layer_scale*torch.ones(in_dim)))
            else:
                self.first_in.append(DenseMLPBlock(layer_dim_coef[i-1],layer_dim_coef[i],drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_in.append(nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[i-1])))
        # self.middle=DenseMLPBlock(layer_dim_coef[-1],layer_dim_coef[-1],drop_rate)
        # self.middle_layer=nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[-1]))
        # self.atten=nn.MultiheadAttention(embed_dim=layer_dim_coef[-1],num_heads=num_heads,dropout=0.8,batch_first=True)
        for i in range(len(layer_dim_coef)-1,-1,-1):
            if(i==0):
                self.first_out.append(DenseMLPBlock(layer_dim_coef[i],in_dim,drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_out.append(nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[i])))
            else:
                self.first_out.append(DenseMLPBlock(layer_dim_coef[i],layer_dim_coef[i-1],drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_out.append(nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[i])))
        self.final=nn.Sequential(
            nn.LayerNorm(in_dim),
            nn.Linear(in_dim,num_classes),
            nn.Softmax()
            )
        self.apply(self._init_weight)
    def _init_weight(self,m):
        if isinstance(m,(nn.Conv1d,nn.Linear)):
            nn.init.trunc_normal_(m.weight,std=0.02)
    def forward(self,x):
        # if(len(x.shape)==3):
        #     x=x.mean(2)#dim
        #x=x.permute(0,2,1)

        x=self.small(x.permute(0,2,1).float()).permute(0,2,1)
        
        #zero=zero.permute(0,2,1)
        #print(zero.shape,self.coef[-1])
        #zero=torch.repeat_interleave(zero,self.coef[-1],2)
        #print(zero.shape,x.shape)
        in_=[]
        in_.append(x*self.layer_parameter_in[0])
        for i in range(len(self.first_in)):
            x=self.first_in[i](x)
            #print(x.shape)
            # if(i!= len(self.layer_parameter_in)-1):
            #     x=x*self.layer_parameter_in[i+1]
            in_.append(x)
        #print(x.shape)
        #x=x.permute(0,2,1)

        # x,_=self.atten(x,zero,x)
        # x=x*self.middle_layer+in_[-1]
        #print(x.shape)
        
        #x=x.permute(0,2,1)
        in_.pop()
        in_.reverse()
        for i in range(len(self.first_out)):
            #x=self.first_out[i](x)
            x=self.first_out[i](x)+in_[i]
        return self.final(x.mean(1))
def train(data_path,random_state=42,epoches=3500,weight_decay=0.05,label_smoothing=0.1):
    path = data_path
    df = pd.read_csv(path+'/metadata/UrbanSound8K.csv')
    extracted = []
    for index_num,row in tqdm(df.iterrows()):
        warnings.filterwarnings('ignore')
        file_name = os.path.join(os.path.abspath(path),'fold'+str(row["fold"])+'/',str(row['slice_file_name'])) 
        final_class_labels = row['class']   
        feature=np.load(os.path.abspath(path)+"/Numpy_4_gfcc_bfcc_mfcc_lfcc_ngcc/"+'fold'+str(row["fold"])+'/'+str(row['slice_file_name']).split('.')[0]+'.npy')
        extracted.append([feature,final_class_labels])
    ext_df = pd.DataFrame(extracted,columns=['feature','class'])
    x_all = np.array(ext_df[['feature']].to_numpy())
    x=[]
    for i in x_all:
        #print(i[0].shape)
        x.append(i[0])
    y = np.array(ext_df['class'].tolist())
    le = LabelEncoder()
    y = le.fit_transform(y)
    y_all=np.eye(10)[y]
    x_train, x_test, y_train, y_test = train_test_split(np.array(x), y_all, test_size=0.2, random_state = random_state)
    print(x_train[0].shape)
    print("Number of training samples = ", x_train.shape[0])
    print("Number of testing samples = ",x_test.shape[0])
    train_model=PIPMN(in_dim=100,num_classes=10,layer_dim_coef=[4,8],drop_rate=0.5,process_lenth=10).cuda()
    print("Number of Parameters: ",sum(i.nelement() for i in train_model.parameters()),0.05)
    optim=torch.optim.AdamW(train_model.parameters(),weight_decay=weight_decay)
    loss=nn.CrossEntropyLoss(label_smoothing=label_smoothing)
    x_train=torch.tensor(x_train).cuda()
    y_train=torch.tensor(y_train).cuda()
    x_test=torch.tensor(x_test).cuda()
    y_test=torch.tensor(y_test).cuda()
    print(x_train.shape,y_train.shape)

    for epoch in  range(epoches) :
        corr=0
        count=0
        train_model.train()
        optim.zero_grad()
        pre=train_model(x_train)
        corr+=sum(torch.argmax(pre,dim=1).cpu().detach().numpy()==torch.argmax(y_train,dim=1).cpu().detach().numpy())
        count+=1
        losses=loss(pre,y_train)
        losses.backward()
        optim.step()
        print(corr,count)
        count=0
        print("train: ",corr/len(x_train))
        corr=0
        train_model.eval()
        test_pre=train_model(x_test)
        corr+=sum(torch.argmax(test_pre,dim=1).cpu().detach().numpy()==torch.argmax(y_test,dim=1).cpu().detach().numpy())
        print("validation dataet accuracy: ",corr/len(y_test))
train("D:/Living_and_Study_In_University/Dataset/UrbanSound8K")

8732it [00:04, 2076.66it/s]


(399, 100)
Number of training samples =  6985
Number of testing samples =  1747
400
800
Number of Parameters:  1454050 0.05
torch.Size([6985, 399, 100]) torch.Size([6985, 10])
770 1
train:  0.11023622047244094
validation dataet accuracy:  0.13222667429879795
773 1
train:  0.11066571224051538
validation dataet accuracy:  0.13394390383514596
781 1
train:  0.11181102362204724
validation dataet accuracy:  0.13795077275329135
797 1
train:  0.11410164638511096
validation dataet accuracy:  0.1522610188895249
968 1
train:  0.13858267716535433
validation dataet accuracy:  0.1619919862621637
1100 1
train:  0.15748031496062992
validation dataet accuracy:  0.15397824842587293
1048 1
train:  0.15003579098067288
validation dataet accuracy:  0.13737836290784203
962 1
train:  0.13772369362920545
validation dataet accuracy:  0.12249570692615913
895 1
train:  0.12813171080887617
validation dataet accuracy:  0.11963365769891242
877 1
train:  0.1255547602004295
validation dataet accuracy:  0.1436748712077

In [19]:
#without 3  0.936
import torch.nn as nn 
import torch
from tqdm import tqdm
from torchlibrosa import Spectrogram,LogmelFilterBank
from torchlibrosa import SpecAugmentation
import torchaudio
import random
import librosa
import pandas as pd
import os
import numpy as np
from tqdm import tqdm
from sklearn.model_selection import train_test_split 
from sklearn.preprocessing import LabelEncoder
import torch.nn as nn
import torch
import IPython.display as ipd
import random
import warnings
from cProfile import label
from itertools import dropwhile
import torch.nn as nn 
import torch
from tqdm import tqdm
from torchlibrosa import Spectrogram,LogmelFilterBank
from torchlibrosa import SpecAugmentation
import torchaudio
import random
from torch.utils.tensorboard import SummaryWriter
writer=SummaryWriter("EventRecord")

class feedforward(nn.Module):
    def __init__(self,in_dim,out_dim,drop_rate=0.5,real_dim=10) -> None:
        super(feedforward,self).__init__()
        self.main=nn.Sequential(
            nn.LayerNorm(in_dim),
            nn.Linear(in_dim,out_dim),
            nn.GELU(),
            nn.Dropout(drop_rate),
            nn.Linear(out_dim,in_dim),
            nn.Dropout(drop_rate),
        )
        self.conv=nn.Conv1d(kernel_size=3,in_channels=real_dim,out_channels=real_dim,padding=1,stride=1,groups=real_dim)
        self.fuse=nn.Sequential(
            nn.Linear(3*in_dim,in_dim),
            nn.Dropout(drop_rate),
        )
    def forward(self,x):
        #print(x.shape)
        x=x.permute(0,2,1)
        proj=self.conv(x)
        #print(proj.shape,x.shape)
        pre=x
        x=self.main(x)+x
        return self.fuse(torch.concat([x,pre,proj],dim=2)).permute(0,2,1)
class DenseMLPBlock(nn.Module):
    def __init__(self,in_dim,out_dim,drop_rate=0.5,layer_scale_init=1e-6,lenth=10,alpha=2) -> None:
        super(DenseMLPBlock,self).__init__()
        self.spa=feedforward(lenth,lenth*alpha,drop_rate=drop_rate,real_dim=in_dim)
        self.li=nn.Sequential(
            nn.LayerNorm(in_dim),
            nn.Linear(in_dim,out_dim),
            nn.GELU(),
            nn.Dropout(drop_rate),)
        self.gamma=nn.Parameter(layer_scale_init*torch.ones(out_dim),requires_grad=True)
        self.gamma_fi=nn.Parameter(layer_scale_init*torch.ones(in_dim))
        self.large=nn.Sequential(
            nn.Linear(in_dim,out_dim,bias=False),
            nn.Dropout(drop_rate),
        )
    def forward(self,x):
        #print(x.shape)
        x=self.gamma_fi*(self.spa(x))+x
        return self.gamma*(self.li(x))
class PIPMN(nn.Module):
    def __init__(self,in_dim=50,num_classes=10,drop_rate=0.5,layer_dim_coef=[4,8],init_layer_scale=1e-6,num_heads=4,process_lenth=1):
        super(PIPMN,self).__init__()
        self.first_in=nn.ModuleList()
        self.first_out=nn.ModuleList()
        self.layer_parameter_in=nn.ParameterList()
        self.layer_parameter_out=nn.ParameterList()
        self.coef=layer_dim_coef.copy()
        self.in_dim=in_dim
        self.small=nn.AdaptiveAvgPool1d(process_lenth)
        final_lenth=process_lenth
        for i in range(len(layer_dim_coef)):
            layer_dim_coef[i]*=in_dim
            print(layer_dim_coef[i])
           
        for i in range(len(layer_dim_coef)):
            if(i==0):
                self.first_in.append(DenseMLPBlock(in_dim,layer_dim_coef[i],drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_in.append(nn.Parameter(init_layer_scale*torch.ones(in_dim)))
            else:
                self.first_in.append(DenseMLPBlock(layer_dim_coef[i-1],layer_dim_coef[i],drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_in.append(nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[i-1])))
        # self.middle=DenseMLPBlock(layer_dim_coef[-1],layer_dim_coef[-1],drop_rate)
        # self.middle_layer=nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[-1]))
        # self.atten=nn.MultiheadAttention(embed_dim=layer_dim_coef[-1],num_heads=num_heads,dropout=0.8,batch_first=True)
        for i in range(len(layer_dim_coef)-1,-1,-1):
            if(i==0):
                self.first_out.append(DenseMLPBlock(layer_dim_coef[i],in_dim,drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_out.append(nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[i])))
            else:
                self.first_out.append(DenseMLPBlock(layer_dim_coef[i],layer_dim_coef[i-1],drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_out.append(nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[i])))
        self.final=nn.Sequential(
            nn.LayerNorm(in_dim),
            nn.Linear(in_dim,num_classes),
            nn.Softmax()
            )
        self.apply(self._init_weight)
    def _init_weight(self,m):
        if isinstance(m,(nn.Conv1d,nn.Linear)):
            nn.init.trunc_normal_(m.weight,std=0.02)
    def forward(self,x):
        # if(len(x.shape)==3):
        #     x=x.mean(2)#dim
        #x=x.permute(0,2,1)

        x=self.small(x.permute(0,2,1).float()).permute(0,2,1)
        
        #zero=zero.permute(0,2,1)
        #print(zero.shape,self.coef[-1])
        #zero=torch.repeat_interleave(zero,self.coef[-1],2)
        #print(zero.shape,x.shape)
        in_=[]
        in_.append(x*self.layer_parameter_in[0])
        for i in range(len(self.first_in)):
            x=self.first_in[i](x)
            #print(x.shape)
            # if(i!= len(self.layer_parameter_in)-1):
            #     x=x*self.layer_parameter_in[i+1]
            in_.append(x)
        #print(x.shape)
        #x=x.permute(0,2,1)

        # x,_=self.atten(x,zero,x)
        # x=x*self.middle_layer+in_[-1]
        #print(x.shape)
        
        #x=x.permute(0,2,1)
        in_.pop()
        in_.reverse()
        for i in range(len(self.first_out)):
            #x=self.first_out[i](x)
            x=self.first_out[i](x)+in_[i]
        return self.final(x.mean(1))
def train(data_path,random_state=42,epoches=3500,weight_decay=0.05,label_smoothing=0.1):
    path = data_path
    df = pd.read_csv(path+'/metadata/UrbanSound8K.csv')
    extracted = []
    for index_num,row in tqdm(df.iterrows()):
        warnings.filterwarnings('ignore')
        file_name = os.path.join(os.path.abspath(path),'fold'+str(row["fold"])+'/',str(row['slice_file_name'])) 
        final_class_labels = row['class']   
        feature=np.load(os.path.abspath(path)+"/Numpy_4_gfcc_bfcc_mfcc_lfcc_ngcc/"+'fold'+str(row["fold"])+'/'+str(row['slice_file_name']).split('.')[0]+'.npy')
        extracted.append([feature,final_class_labels])
    ext_df = pd.DataFrame(extracted,columns=['feature','class'])
    x_all = np.array(ext_df[['feature']].to_numpy())
    x=[]
    for i in x_all:
        #print(i[0].shape)
        x.append(i[0])
    y = np.array(ext_df['class'].tolist())
    le = LabelEncoder()
    y = le.fit_transform(y)
    y_all=np.eye(10)[y]
    x_train, x_test, y_train, y_test = train_test_split(np.array(x), y_all, test_size=0.2, random_state = random_state)
    print(x_train[0].shape)
    print("Number of training samples = ", x_train.shape[0])
    print("Number of testing samples = ",x_test.shape[0])
    train_model=PIPMN(in_dim=100,num_classes=10,layer_dim_coef=[4,8],drop_rate=0.5,process_lenth=10).cuda()
    print("Number of Parameters: ",sum(i.nelement() for i in train_model.parameters()),0.05)
    optim=torch.optim.AdamW(train_model.parameters(),weight_decay=weight_decay)
    loss=nn.CrossEntropyLoss(label_smoothing=label_smoothing)
    x_train=torch.tensor(x_train).cuda()
    y_train=torch.tensor(y_train).cuda()
    x_test=torch.tensor(x_test).cuda()
    y_test=torch.tensor(y_test).cuda()
    print(x_train.shape,y_train.shape)

    for epoch in  range(epoches) :
        corr=0
        count=0
        train_model.train()
        optim.zero_grad()
        pre=train_model(x_train)
        corr+=sum(torch.argmax(pre,dim=1).cpu().detach().numpy()==torch.argmax(y_train,dim=1).cpu().detach().numpy())
        count+=1
        losses=loss(pre,y_train)
        losses.backward()
        optim.step()
        print(corr,count)
        count=0
        print("train: ",corr/len(x_train))
        corr=0
        train_model.eval()
        test_pre=train_model(x_test)
        corr+=sum(torch.argmax(test_pre,dim=1).cpu().detach().numpy()==torch.argmax(y_test,dim=1).cpu().detach().numpy())
        print("validation dataet accuracy: ",corr/len(y_test))
train("D:/Living_and_Study_In_University/Dataset/UrbanSound8K")

8732it [00:03, 2290.99it/s]


(399, 100)
Number of training samples =  6985
Number of testing samples =  1747
400
800
Number of Parameters:  1461250 0.05
torch.Size([6985, 399, 100]) torch.Size([6985, 10])
764 1
train:  0.10937723693629206
validation dataet accuracy:  0.11619919862621637
796 1
train:  0.11395848246241946
validation dataet accuracy:  0.13909559244419004
953 1
train:  0.1364352183249821
validation dataet accuracy:  0.1511161991986262
1144 1
train:  0.16377952755905512
validation dataet accuracy:  0.14481969089868346
1178 1
train:  0.1686471009305655
validation dataet accuracy:  0.1505437893531769
1215 1
train:  0.1739441660701503
validation dataet accuracy:  0.16027475672581568
1226 1
train:  0.17551896921975663
validation dataet accuracy:  0.1848883800801374
1376 1
train:  0.1969935576234789
validation dataet accuracy:  0.22381224957069262
1711 1
train:  0.24495347172512527
validation dataet accuracy:  0.28105323411562677
2039 1
train:  0.29191123836793126
validation dataet accuracy:  0.275329135661

In [2]:
#Original Multi Stage   0.936
random_state=42
import torch.nn as nn 
import torch
from tqdm import tqdm
from torchlibrosa import Spectrogram,LogmelFilterBank
from torchlibrosa import SpecAugmentation
import torchaudio
import random
import librosa
import pandas as pd
import os
import numpy as np
from tqdm import tqdm
from sklearn.model_selection import train_test_split 
from sklearn.preprocessing import LabelEncoder
import torch.nn as nn
import torch
import IPython.display as ipd
import random
import warnings
from cProfile import label
from itertools import dropwhile
import torch.nn as nn 
import torch
from tqdm import tqdm
from torchlibrosa import Spectrogram,LogmelFilterBank
from torchlibrosa import SpecAugmentation
import torchaudio
import random
from torch.utils.tensorboard import SummaryWriter
#Audio Single
from torch.utils.tensorboard import SummaryWriter
from torch.utils.data import DataLoader,Dataset
from torch.utils.tensorboard import SummaryWriter
writer=SummaryWriter("EventRecord")

class feedforward(nn.Module):
    def __init__(self,in_dim,out_dim,drop_rate=0.5,real_dim=10) -> None:
        super(feedforward,self).__init__()
        self.main=nn.Sequential(
            nn.LayerNorm(in_dim),
            nn.Linear(in_dim,out_dim),
            nn.GELU(),
            nn.Dropout(drop_rate),
            nn.Linear(out_dim,in_dim),
            nn.Dropout(drop_rate),
        )
        self.conv=nn.Conv1d(kernel_size=3,in_channels=real_dim,out_channels=real_dim,padding=1,stride=1,groups=real_dim)
        self.fuse=nn.Sequential(
            nn.Linear(3*in_dim,in_dim),
            nn.Dropout(drop_rate),
        )
    def forward(self,x):
        #print(x.shape)
        x=x.permute(0,2,1)
        proj=self.conv(x)
        #print(proj.shape,x.shape)
        pre=x
        x=self.main(x)+x
        return self.fuse(torch.concat([x,pre,proj],dim=2)).permute(0,2,1)
class DenseMLPBlock(nn.Module):
    def __init__(self,in_dim,out_dim,drop_rate=0.5,layer_scale_init=1e-6,lenth=10,alpha=2) -> None:
        super(DenseMLPBlock,self).__init__()
        self.spa=feedforward(lenth,lenth*alpha,drop_rate=drop_rate,real_dim=in_dim)
        self.li=nn.Sequential(
            nn.LayerNorm(in_dim),
            nn.Linear(in_dim,out_dim),
            nn.GELU(),
            nn.Dropout(drop_rate),)
        self.gamma=nn.Parameter(layer_scale_init*torch.ones(out_dim),requires_grad=True)
        self.gamma_fi=nn.Parameter(layer_scale_init*torch.ones(in_dim))
        self.large=nn.Sequential(
            nn.Linear(in_dim,out_dim,bias=False),
            nn.Dropout(drop_rate),
        )
    def forward(self,x):
        #print(x.shape)
        x=self.gamma_fi*(self.spa(x))+x
        return self.gamma*(self.li(x)+self.large(x))
class PIPMN(nn.Module):
    def __init__(self,in_dim=50,num_classes=10,drop_rate=0.5,layer_dim_coef=[4,4,8,8],init_layer_scale=1e-6,num_heads=4,process_lenth=1):
        super(PIPMN,self).__init__()
        self.first_in=nn.ModuleList()
        self.first_out=nn.ModuleList()
        self.layer_parameter_in=nn.ParameterList()
        self.layer_parameter_out=nn.ParameterList()
        self.coef=layer_dim_coef.copy()
        self.in_dim=in_dim
        self.small=nn.AdaptiveAvgPool1d(process_lenth)
        final_lenth=process_lenth
        print(layer_dim_coef)
        for i in range(len(layer_dim_coef)):
            layer_dim_coef[i]*=in_dim
            print(layer_dim_coef[i])
           
        for i in range(len(layer_dim_coef)):
            if(i==0):
                self.first_in.append(DenseMLPBlock(in_dim,layer_dim_coef[i],drop_rate=drop_rate,lenth=final_lenth).cuda())
                self.layer_parameter_in.append(nn.Parameter((init_layer_scale*torch.ones(in_dim)).cuda()))
            else:
                self.first_in.append(DenseMLPBlock(layer_dim_coef[i-1],layer_dim_coef[i],drop_rate=drop_rate,lenth=final_lenth).cuda())
                self.layer_parameter_in.append(nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[i-1])).cuda())
        # self.middle=DenseMLPBlock(layer_dim_coef[-1],layer_dim_coef[-1],drop_rate)
        # self.middle_layer=nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[-1]))
        # self.atten=nn.MultiheadAttention(embed_dim=layer_dim_coef[-1],num_heads=num_heads,dropout=0.8,batch_first=True)
        self.final=nn.Sequential(
            nn.LayerNorm(layer_dim_coef[-1]),
            nn.Linear(layer_dim_coef[-1],num_classes),
            nn.Softmax()
            )
        self.apply(self._init_weight)
    def _init_weight(self,m):
        if isinstance(m,(nn.Conv1d,nn.Linear)):
            nn.init.trunc_normal_(m.weight,std=0.02)
    def forward(self,x):
        # if(len(x.shape)==3):
        #     x=x.mean(2)#dim
        #x=x.permute(0,2,1)

        x=self.small(x.permute(0,2,1).float()).permute(0,2,1)
        
        #zero=zero.permute(0,2,1)
        #print(zero.shape,self.coef[-1])
        #zero=torch.repeat_interleave(zero,self.coef[-1],2)
        #print(zero.shape,x.shape)
        for i in range(len(self.first_in)):
            x=self.first_in[i](x)
            #print(x.shape)
            # if(i!= len(self.layer_parameter_in)-1):
            #     x=x*self.layer_parameter_in[i+1]
        #print(x.shape)
        #x=x.permute(0,2,1)

        # x,_=self.atten(x,zero,x)
        # x=x*self.middle_layer+in_[-1]
        #print(x.shape)
        
        #x=x.permute(0,2,1)
        return self.final(x.mean(1))
class UB8(Dataset):
    def __init__(self,path="D:/Living_and_Study_In_University/Dataset/UrbanSound8K",random_state=42,train=True):
        super(UB8,self).__init__()
        self.path=path
        self.random_state=random_state
        self.train=train
        self.df = pd.read_csv(self.path+'/metadata/UrbanSound8K.csv')
        extracted = []
        for index_num,row in tqdm(self.df.iterrows()):
            warnings.filterwarnings('ignore')
            file_name = os.path.join(os.path.abspath(self.path),'fold'+str(row["fold"])+'/',str(row['slice_file_name'])) 
            final_class_labels = row['class']   
            feature=np.load(os.path.abspath(self.path)+"/Numpy_4_gfcc_bfcc_mfcc_lfcc_ngcc/"+'fold'+str(row["fold"])+'/'+str(row['slice_file_name']).split('.')[0]+'.npy')
            extracted.append([feature,final_class_labels])
        ext_df = pd.DataFrame(extracted,columns=['feature','class'])
        x_all = np.array(ext_df[['feature']].to_numpy())
        x=[]
        for i in x_all:
            #print(i[0].shape)
            x.append(i[0])
        y = np.array(ext_df['class'].tolist())
        le = LabelEncoder()
        y = le.fit_transform(y)
        y_all=np.eye(10)[y]
        x_train, x_test, y_train, y_test = train_test_split(np.array(x), y_all, test_size=0.2, random_state = self.random_state)
        if self.train:
            self.x=torch.tensor(x_train).float()
            self.y=y_train
        else:
            self.x=torch.tensor(x_test).float()
            self.y=y_test
    def __getitem__(self,index):
        return self.x[index],self.y[index]
    def __len__(self):
        return len(self.x)
train_dataset=UB8(train=True,random_state=random_state)
test_dataset=UB8(train=False,random_state=random_state)
batch_size=1280
model=PIPMN(in_dim=100,num_classes=10,layer_dim_coef=[4,4,8,8],drop_rate=0.5,process_lenth=5).cuda()
loss_function=nn.CrossEntropyLoss(label_smoothing=0.1)
optimizer=torch.optim.AdamW(model.parameters(),lr=0.001)
model.cuda()
model.train()
epoches=3500
wrtier=SummaryWriter("Classification")
count=0
for epoch in range(epoches):
    all_correct=0
    all_cnt=0
    model.train()
    train_loader=DataLoader(train_dataset,batch_size=batch_size,shuffle=True)
    test_loader=DataLoader(test_dataset,batch_size=batch_size,shuffle=True)
    for index,(data,label) in enumerate(train_loader):
        if(count<=2):
            print(data.shape)
            count+=1
        data=data.cuda()
        label=label.cuda()
        optimizer.zero_grad()
        output=model(data)
        all_cnt+=data.shape[0]
        loss=loss_function(output,label)
        all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
        loss.backward()
        optimizer.step()
        #wrtier.add_scalar("Train_loss_Single_Modal",loss,index+epoch*len(train_loader))
        #wrtier.add_scalar("Train_accuracy_Single_Modal",all_correct/(all_cnt),index+epoch*len(train_loader))

    print("Epoch: ",epoch,"Train Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)
        
    model.eval()
    with torch.no_grad():
        all_correct=0
        all_cnt=0
        for index,(data,label) in enumerate(test_loader):
            if(count<=2):
                print(data.shape)
                count+=1
            data=data.cuda()
            label=label.cuda()
            output=model(data)
            all_cnt+=data.shape[0]
            all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
            loss=loss_function(output,label)
            #wrtier.add_scalar("Test_accuracy_Single_Modal",all_correct/(all_cnt),epoch)
            #wrtier.add_scalar("Test_loss_Single_Modal",loss,epoch)
        print("Epoch: ",epoch,"Test Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)

8732it [00:02, 2941.50it/s]
8732it [00:02, 3020.86it/s]


[4, 4, 8, 8]
400
400
800
800
torch.Size([1280, 399, 100])
torch.Size([1280, 399, 100])
torch.Size([1280, 399, 100])
Epoch:  0 Train Accuracy:  tensor(0.0948, device='cuda:0')  Loss:  tensor(2.2954, device='cuda:0', dtype=torch.float64, grad_fn=<DivBackward1>)
Epoch:  0 Test Accuracy:  tensor(0.1162, device='cuda:0')  Loss:  tensor(2.2869, device='cuda:0', dtype=torch.float64)
Epoch:  1 Train Accuracy:  tensor(0.1326, device='cuda:0')  Loss:  tensor(2.2767, device='cuda:0', dtype=torch.float64, grad_fn=<DivBackward1>)
Epoch:  1 Test Accuracy:  tensor(0.1820, device='cuda:0')  Loss:  tensor(2.2461, device='cuda:0', dtype=torch.float64)
Epoch:  2 Train Accuracy:  tensor(0.1999, device='cuda:0')  Loss:  tensor(2.2103, device='cuda:0', dtype=torch.float64, grad_fn=<DivBackward1>)
Epoch:  2 Test Accuracy:  tensor(0.2484, device='cuda:0')  Loss:  tensor(2.1857, device='cuda:0', dtype=torch.float64)
Epoch:  3 Train Accuracy:  tensor(0.2826, device='cuda:0')  Loss:  tensor(2.1435, device='cuda:

In [ ]:
import librosa
import pandas as pd
import os
import numpy as np
from tqdm import tqdm
from sklearn.model_selection import train_test_split 
from sklearn.preprocessing import LabelEncoder
import torch.nn as nn
import torch
import IPython.display as ipd
import random
import warnings
from cProfile import label
from itertools import dropwhile
import torch.nn as nn 
import torch
from tqdm import tqdm
from torchlibrosa import Spectrogram,LogmelFilterBank
from torchlibrosa import SpecAugmentation
import torchaudio
import random
from torch.utils.tensorboard import SummaryWriter
#Audio Single
from torch.utils.tensorboard import SummaryWriter
from torch.utils.data import DataLoader,Dataset
model=PIPMN(in_dim=100,num_classes=10,layer_dim_coef=[4,8],drop_rate=0.5,process_lenth=5).cuda()
from torch.utils.data import DataLoader,Dataset
class UB8(Dataset):
    def __init__(self,path="D:/Living_and_Study_In_University/Dataset/UrbanSound8K",random_state=42,train=True):
        super(UB8,self).__init__()
        self.path=path
        self.random_state=random_state
        self.train=train
        self.df = pd.read_csv(self.path+'/metadata/UrbanSound8K.csv')
        extracted = []
        for index_num,row in tqdm(self.df.iterrows()):
            warnings.filterwarnings('ignore')
            file_name = os.path.join(os.path.abspath(self.path),'fold'+str(row["fold"])+'/',str(row['slice_file_name'])) 
            final_class_labels = row['class']   
            feature=np.load(os.path.abspath(self.path)+"/Numpy_4_gfcc_bfcc_mfcc_lfcc_ngcc/"+'fold'+str(row["fold"])+'/'+str(row['slice_file_name']).split('.')[0]+'.npy')
            extracted.append([feature,final_class_labels])
        ext_df = pd.DataFrame(extracted,columns=['feature','class'])
        x_all = np.array(ext_df[['feature']].to_numpy())
        x=[]
        for i in x_all:
            #print(i[0].shape)
            x.append(i[0])
        y = np.array(ext_df['class'].tolist())
        le = LabelEncoder()
        y = le.fit_transform(y)
        y_all=np.eye(10)[y]
        x_train, x_test, y_train, y_test = train_test_split(np.array(x), y_all, test_size=0.2, random_state = self.random_state)
        if self.train:
            self.x=torch.tensor(x_train).float()
            self.y=y_train
        else:
            self.x=torch.tensor(x_test).float()
            self.y=y_test
    def __getitem__(self,index):
        return self.x[index],self.y[index]
    def __len__(self):
        return len(self.x)
train_dataset=UB8(train=True)
test_dataset=UB8(train=False)
batch_size=len(train_dataset)
train_loader=DataLoader(train_dataset,batch_size=batch_size,shuffle=True)
test_loader=DataLoader(test_dataset,batch_size=batch_size,shuffle=True)
loss_function=nn.CrossEntropyLoss(label_smoothing=0.1)
optimizer=torch.optim.AdamW(model.parameters(),lr=0.001)
model.cuda()
model.train()
epoches=3500
wrtier=SummaryWriter("Classification")
count=0
for epoch in range(epoches):
    all_correct=0
    all_cnt=0
    model.train()
    for index,(data,label) in enumerate(train_loader):
        if(count<=2):
            print(data.shape)
            count+=1
        data=data.cuda()
        label=label.cuda()
        optimizer.zero_grad()
        output=model(data)
        all_cnt+=data.shape[0]
        loss=loss_function(output,label)
        all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
        loss.backward()
        optimizer.step()
        #wrtier.add_scalar("Train_loss_Single_Modal",loss,index+epoch*len(train_loader))
        #wrtier.add_scalar("Train_accuracy_Single_Modal",all_correct/(all_cnt),index+epoch*len(train_loader))

    print("Epoch: ",epoch,"Train Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)
        
    model.eval()
    with torch.no_grad():
        all_correct=0
        all_cnt=0
        for index,(data,label) in enumerate(test_loader):
            if(count<=2):
                print(data.shape)
                count+=1
            data=data.cuda()
            label=label.cuda()
            output=model(data)
            all_cnt+=data.shape[0]
            all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
            loss=loss_function(output,label)
            #wrtier.add_scalar("Test_accuracy_Single_Modal",all_correct/(all_cnt),epoch)
            #wrtier.add_scalar("Test_loss_Single_Modal",loss,epoch)
        print("Epoch: ",epoch,"Test Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)

In [21]:
#mel spectrom  0.921
import torch.nn as nn 
import torch
from tqdm import tqdm
from torchlibrosa import Spectrogram,LogmelFilterBank
from torchlibrosa import SpecAugmentation
import torchaudio
import random
import librosa
import pandas as pd
import os
import numpy as np
from tqdm import tqdm
from sklearn.model_selection import train_test_split 
from sklearn.preprocessing import LabelEncoder
import torch.nn as nn
import torch
import IPython.display as ipd
import random
import warnings
from cProfile import label
from itertools import dropwhile
import torch.nn as nn 
import torch
from tqdm import tqdm
from torchlibrosa import Spectrogram,LogmelFilterBank
from torchlibrosa import SpecAugmentation
import torchaudio
import random
from torch.utils.tensorboard import SummaryWriter
writer=SummaryWriter("EventRecord")

class feedforward(nn.Module):
    def __init__(self,in_dim,out_dim,drop_rate=0.5,real_dim=10) -> None:
        super(feedforward,self).__init__()
        self.main=nn.Sequential(
            nn.LayerNorm(in_dim),
            nn.Linear(in_dim,out_dim),
            nn.GELU(),
            nn.Dropout(drop_rate),
            nn.Linear(out_dim,in_dim),
            nn.Dropout(drop_rate),
        )
        self.conv=nn.Conv1d(kernel_size=3,in_channels=real_dim,out_channels=real_dim,padding=1,stride=1,groups=real_dim)
        self.fuse=nn.Sequential(
            nn.Linear(3*in_dim,in_dim),
            nn.Dropout(drop_rate),
        )
    def forward(self,x):
        #print(x.shape)
        x=x.permute(0,2,1)
        proj=self.conv(x)
        #print(proj.shape,x.shape)
        pre=x
        x=self.main(x)+x
        return self.fuse(torch.concat([x,pre,proj],dim=2)).permute(0,2,1)
class DenseMLPBlock(nn.Module):
    def __init__(self,in_dim,out_dim,drop_rate=0.5,layer_scale_init=1e-6,lenth=10,alpha=2) -> None:
        super(DenseMLPBlock,self).__init__()
        self.spa=feedforward(lenth,lenth*alpha,drop_rate=drop_rate,real_dim=in_dim)
        self.li=nn.Sequential(
            nn.LayerNorm(in_dim),
            nn.Linear(in_dim,out_dim),
            nn.GELU(),
            nn.Dropout(drop_rate),)
        self.gamma=nn.Parameter(layer_scale_init*torch.ones(out_dim),requires_grad=True)
        self.gamma_fi=nn.Parameter(layer_scale_init*torch.ones(in_dim))
        self.large=nn.Sequential(
            nn.Linear(in_dim,out_dim,bias=False),
            nn.Dropout(drop_rate),
        )
    def forward(self,x):
        #print(x.shape)
        x=self.gamma_fi*(self.spa(x))+x
        return self.gamma*(self.li(x)+self.large(x))
class PIPMN(nn.Module):
    def __init__(self,in_dim=50,num_classes=10,drop_rate=0.5,layer_dim_coef=[4,8],init_layer_scale=1e-6,num_heads=4,process_lenth=1):
        super(PIPMN,self).__init__()
        self.first_in=nn.ModuleList()
        self.first_out=nn.ModuleList()
        self.layer_parameter_in=nn.ParameterList()
        self.layer_parameter_out=nn.ParameterList()
        self.coef=layer_dim_coef.copy()
        self.in_dim=in_dim
        self.small=nn.AdaptiveAvgPool1d(process_lenth)
        final_lenth=process_lenth
        for i in range(len(layer_dim_coef)):
            layer_dim_coef[i]*=in_dim
            print(layer_dim_coef[i])
           
        for i in range(len(layer_dim_coef)):
            if(i==0):
                self.first_in.append(DenseMLPBlock(in_dim,layer_dim_coef[i],drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_in.append(nn.Parameter(init_layer_scale*torch.ones(in_dim)))
            else:
                self.first_in.append(DenseMLPBlock(layer_dim_coef[i-1],layer_dim_coef[i],drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_in.append(nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[i-1])))
        # self.middle=DenseMLPBlock(layer_dim_coef[-1],layer_dim_coef[-1],drop_rate)
        # self.middle_layer=nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[-1]))
        # self.atten=nn.MultiheadAttention(embed_dim=layer_dim_coef[-1],num_heads=num_heads,dropout=0.8,batch_first=True)
        for i in range(len(layer_dim_coef)-1,-1,-1):
            if(i==0):
                self.first_out.append(DenseMLPBlock(layer_dim_coef[i],in_dim,drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_out.append(nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[i])))
            else:
                self.first_out.append(DenseMLPBlock(layer_dim_coef[i],layer_dim_coef[i-1],drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_out.append(nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[i])))
        self.final=nn.Sequential(
            nn.LayerNorm(in_dim),
            nn.Linear(in_dim,num_classes),
            nn.Softmax()
            )
        self.apply(self._init_weight)
    def _init_weight(self,m):
        if isinstance(m,(nn.Conv1d,nn.Linear)):
            nn.init.trunc_normal_(m.weight,std=0.02)
    def forward(self,x):
        # if(len(x.shape)==3):
        #     x=x.mean(2)#dim
        #x=x.permute(0,2,1)

        x=self.small(x.permute(0,2,1).float()).permute(0,2,1)
        
        #zero=zero.permute(0,2,1)
        #print(zero.shape,self.coef[-1])
        #zero=torch.repeat_interleave(zero,self.coef[-1],2)
        #print(zero.shape,x.shape)
        in_=[]
        in_.append(x*self.layer_parameter_in[0])
        for i in range(len(self.first_in)):
            x=self.first_in[i](x)
            #print(x.shape)
            # if(i!= len(self.layer_parameter_in)-1):
            #     x=x*self.layer_parameter_in[i+1]
            in_.append(x)
        #print(x.shape)
        #x=x.permute(0,2,1)

        # x,_=self.atten(x,zero,x)
        # x=x*self.middle_layer+in_[-1]
        #print(x.shape)
        
        #x=x.permute(0,2,1)
        in_.pop()
        in_.reverse()
        for i in range(len(self.first_out)):
            #x=self.first_out[i](x)
            x=self.first_out[i](x)+in_[i]
        return self.final(x.mean(1))
def train(data_path,random_state=42,epoches=3500,weight_decay=0.05,label_smoothing=0.1):
    path = data_path
    df = pd.read_csv(path+'/metadata/UrbanSound8K.csv')
    extracted = []
    for index_num,row in tqdm(df.iterrows()):
        warnings.filterwarnings('ignore')
        file_name = os.path.join(os.path.abspath(path),'fold'+str(row["fold"])+'/',str(row['slice_file_name'])) 
        final_class_labels = row['class']   
        feature=np.load(os.path.abspath(path)+"/Mel/"+'fold'+str(row["fold"])+'/'+str(row['slice_file_name']).split('.')[0]+'.npy')
        extracted.append([feature,final_class_labels])
    ext_df = pd.DataFrame(extracted,columns=['feature','class'])
    x_all = np.array(ext_df[['feature']].to_numpy())
    x=[]
    for i in x_all:
        #print(i[0].shape)
        x.append(i[0])
    y = np.array(ext_df['class'].tolist())
    le = LabelEncoder()
    y = le.fit_transform(y)
    y_all=np.eye(10)[y]
    x_train, x_test, y_train, y_test = train_test_split(np.array(x), y_all, test_size=0.2, random_state = random_state)
    print(x_train[0].shape)
    print("Number of training samples = ", x_train.shape[0])
    print("Number of testing samples = ",x_test.shape[0])
    train_model=PIPMN(in_dim=100,num_classes=10,layer_dim_coef=[4,8],drop_rate=0.5,process_lenth=10).cuda()
    print("Number of Parameters: ",sum(i.nelement() for i in train_model.parameters()),0.05)
    optim=torch.optim.AdamW(train_model.parameters(),weight_decay=weight_decay)
    loss=nn.CrossEntropyLoss(label_smoothing=label_smoothing)
    x_train=torch.tensor(x_train).cuda().permute(0,2,1)
    y_train=torch.tensor(y_train).cuda()
    x_test=torch.tensor(x_test).cuda().permute(0,2,1)
    y_test=torch.tensor(y_test).cuda()
    print(x_train.shape,y_train.shape)

    for epoch in  range(epoches) :
        corr=0
        count=0
        train_model.train()
        optim.zero_grad()
        pre=train_model(x_train)
        corr+=sum(torch.argmax(pre,dim=1).cpu().detach().numpy()==torch.argmax(y_train,dim=1).cpu().detach().numpy())
        count+=1
        losses=loss(pre,y_train)
        losses.backward()
        optim.step()
        print(corr,count)
        count=0
        print("train: ",corr/len(x_train))
        corr=0
        train_model.eval()
        test_pre=train_model(x_test)
        corr+=sum(torch.argmax(test_pre,dim=1).cpu().detach().numpy()==torch.argmax(y_test,dim=1).cpu().detach().numpy())
        print("validation dataet accuracy: ",corr/len(y_test))
train("D:/Living_and_Study_In_University/Dataset/UrbanSound8K")

8732it [00:02, 4051.85it/s]


(100, 173)
Number of training samples =  6985
Number of testing samples =  1747
400
800
Number of Parameters:  1461250 0.05
torch.Size([6985, 173, 100]) torch.Size([6985, 10])
817 1
train:  0.11696492483894058
validation dataet accuracy:  0.23983972524327418
1735 1
train:  0.24838940586972083
validation dataet accuracy:  0.2673153978248426
1904 1
train:  0.2725841088045812
validation dataet accuracy:  0.2621637092157985
1972 1
train:  0.282319255547602
validation dataet accuracy:  0.28105323411562677
2057 1
train:  0.29448818897637796
validation dataet accuracy:  0.2976531196336577
2136 1
train:  0.30579813886900503
validation dataet accuracy:  0.31539782484258727
2204 1
train:  0.31553328561202576
validation dataet accuracy:  0.3279908414424728
2265 1
train:  0.3242662848962062
validation dataet accuracy:  0.3342873497424156
2313 1
train:  0.3311381531853973
validation dataet accuracy:  0.341728677733257
2343 1
train:  0.3354330708661417
validation dataet accuracy:  0.3451631368059530

In [14]:
#mfcc  0.953
import torch.nn as nn 
import torch
from tqdm import tqdm
from torchlibrosa import Spectrogram,LogmelFilterBank
from torchlibrosa import SpecAugmentation
import torchaudio
import random
import librosa
import pandas as pd
import os
import numpy as np
from tqdm import tqdm
from sklearn.model_selection import train_test_split 
from sklearn.preprocessing import LabelEncoder
import torch.nn as nn
import torch
import IPython.display as ipd
import random
import warnings
from cProfile import label
from itertools import dropwhile
import torch.nn as nn 
import torch
from tqdm import tqdm
from torchlibrosa import Spectrogram,LogmelFilterBank
from torchlibrosa import SpecAugmentation
import torchaudio
import random
from torch.utils.tensorboard import SummaryWriter
writer=SummaryWriter("EventRecord")

class feedforward(nn.Module):
    def __init__(self,in_dim,out_dim,drop_rate=0.5,real_dim=10) -> None:
        super(feedforward,self).__init__()
        self.main=nn.Sequential(
            nn.LayerNorm(in_dim),
            nn.Linear(in_dim,out_dim),
            nn.GELU(),
            nn.Dropout(drop_rate),
            nn.Linear(out_dim,in_dim),
            nn.Dropout(drop_rate),
        )
        self.conv=nn.Conv1d(kernel_size=3,in_channels=real_dim,out_channels=real_dim,padding=1,stride=1,groups=real_dim)
        self.fuse=nn.Sequential(
            nn.Linear(3*in_dim,in_dim),
            nn.Dropout(drop_rate),
        )
    def forward(self,x):
        #print(x.shape)
        x=x.permute(0,2,1)
        proj=self.conv(x)
        #print(proj.shape,x.shape)
        pre=x
        x=self.main(x)+x
        return self.fuse(torch.concat([x,pre,proj],dim=2)).permute(0,2,1)
class DenseMLPBlock(nn.Module):
    def __init__(self,in_dim,out_dim,drop_rate=0.5,layer_scale_init=1e-6,lenth=10,alpha=2) -> None:
        super(DenseMLPBlock,self).__init__()
        self.spa=feedforward(lenth,lenth*alpha,drop_rate=drop_rate,real_dim=in_dim)
        self.li=nn.Sequential(
            nn.LayerNorm(in_dim),
            nn.Linear(in_dim,out_dim),
            nn.GELU(),
            nn.Dropout(drop_rate),)
        self.gamma=nn.Parameter(layer_scale_init*torch.ones(out_dim),requires_grad=True)
        self.gamma_fi=nn.Parameter(layer_scale_init*torch.ones(in_dim))
        self.large=nn.Sequential(
            nn.Linear(in_dim,out_dim,bias=False),
            nn.Dropout(drop_rate),
        )
    def forward(self,x):
        #print(x.shape)
        x=self.gamma_fi*(self.spa(x))+x
        return self.gamma*(self.li(x)+self.large(x))
class PIPMN(nn.Module):
    def __init__(self,in_dim=50,num_classes=10,drop_rate=0.5,layer_dim_coef=[4,8],init_layer_scale=1e-6,num_heads=4,process_lenth=1):
        super(PIPMN,self).__init__()
        self.first_in=nn.ModuleList()
        self.first_out=nn.ModuleList()
        self.layer_parameter_in=nn.ParameterList()
        self.layer_parameter_out=nn.ParameterList()
        self.coef=layer_dim_coef.copy()
        self.in_dim=in_dim
        self.small=nn.AdaptiveAvgPool1d(process_lenth)
        final_lenth=process_lenth
        for i in range(len(layer_dim_coef)):
            layer_dim_coef[i]*=in_dim
            print(layer_dim_coef[i])
           
        for i in range(len(layer_dim_coef)):
            if(i==0):
                self.first_in.append(DenseMLPBlock(in_dim,layer_dim_coef[i],drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_in.append(nn.Parameter(init_layer_scale*torch.ones(in_dim)))
            else:
                self.first_in.append(DenseMLPBlock(layer_dim_coef[i-1],layer_dim_coef[i],drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_in.append(nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[i-1])))
        # self.middle=DenseMLPBlock(layer_dim_coef[-1],layer_dim_coef[-1],drop_rate)
        # self.middle_layer=nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[-1]))
        # self.atten=nn.MultiheadAttention(embed_dim=layer_dim_coef[-1],num_heads=num_heads,dropout=0.8,batch_first=True)
        for i in range(len(layer_dim_coef)-1,-1,-1):
            if(i==0):
                self.first_out.append(DenseMLPBlock(layer_dim_coef[i],in_dim,drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_out.append(nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[i])))
            else:
                self.first_out.append(DenseMLPBlock(layer_dim_coef[i],layer_dim_coef[i-1],drop_rate=drop_rate,lenth=final_lenth))
                self.layer_parameter_out.append(nn.Parameter(init_layer_scale*torch.ones(layer_dim_coef[i])))
        self.final=nn.Sequential(
            nn.LayerNorm(in_dim),
            nn.Linear(in_dim,num_classes),
            nn.Softmax()
            )
        self.apply(self._init_weight)
    def _init_weight(self,m):
        if isinstance(m,(nn.Conv1d,nn.Linear)):
            nn.init.trunc_normal_(m.weight,std=0.02)
    def forward(self,x):
        # if(len(x.shape)==3):
        #     x=x.mean(2)#dim
        #x=x.permute(0,2,1)

        x=self.small(x.permute(0,2,1).float()).permute(0,2,1)
        
        #zero=zero.permute(0,2,1)
        #print(zero.shape,self.coef[-1])
        #zero=torch.repeat_interleave(zero,self.coef[-1],2)
        #print(zero.shape,x.shape)
        in_=[]
        in_.append(x*self.layer_parameter_in[0])
        for i in range(len(self.first_in)):
            x=self.first_in[i](x)
            #print(x.shape)
            # if(i!= len(self.layer_parameter_in)-1):
            #     x=x*self.layer_parameter_in[i+1]
            in_.append(x)
        #print(x.shape)
        #x=x.permute(0,2,1)

        # x,_=self.atten(x,zero,x)
        # x=x*self.middle_layer+in_[-1]
        #print(x.shape)
        
        #x=x.permute(0,2,1)
        in_.pop()
        in_.reverse()
        for i in range(len(self.first_out)):
            #x=self.first_out[i](x)
            x=self.first_out[i](x)+in_[i]
        return self.final(x.mean(1))
def train(data_path,random_state=42,epoches=3500,weight_decay=0.05,label_smoothing=0.1):
    path = data_path
    df = pd.read_csv(path+'/metadata/UrbanSound8K.csv')
    extracted = []
    for index_num,row in tqdm(df.iterrows()):
        warnings.filterwarnings('ignore')
        file_name = os.path.join(os.path.abspath(path),'fold'+str(row["fold"])+'/',str(row['slice_file_name'])) 
        final_class_labels = row['class']   
        feature=np.load(os.path.abspath(path)+"/mfcc/"+'fold'+str(row["fold"])+'/'+str(row['slice_file_name']).split('.')[0]+'.npy')
        extracted.append([feature,final_class_labels])
    ext_df = pd.DataFrame(extracted,columns=['feature','class'])
    x_all = np.array(ext_df[['feature']].to_numpy())
    x=[]
    for i in x_all:
        #print(i[0].shape)
        x.append(i[0])
    y = np.array(ext_df['class'].tolist())
    le = LabelEncoder()
    y = le.fit_transform(y)
    y_all=np.eye(10)[y]
    x_train, x_test, y_train, y_test = train_test_split(np.array(x), y_all, test_size=0.2, random_state = random_state)
    print(x_train[0].shape)
    print("Number of training samples = ", x_train.shape[0])
    print("Number of testing samples = ",x_test.shape[0])
    train_model=PIPMN(in_dim=50,num_classes=10,layer_dim_coef=[4,8],drop_rate=0.5,process_lenth=10).cuda()
    print("Number of Parameters: ",sum(i.nelement() for i in train_model.parameters()),0.05)
    optim=torch.optim.AdamW(train_model.parameters(),weight_decay=weight_decay)
    loss=nn.CrossEntropyLoss(label_smoothing=label_smoothing)
    x_train=torch.tensor(x_train).cuda().permute(0,2,1)
    y_train=torch.tensor(y_train).cuda()
    x_test=torch.tensor(x_test).cuda().permute(0,2,1)
    y_test=torch.tensor(y_test).cuda()
    print(x_train.shape,y_train.shape)

    for epoch in  range(epoches) :
        corr=0
        count=0
        train_model.train()
        optim.zero_grad()
        pre=train_model(x_train)
        corr+=sum(torch.argmax(pre,dim=1).cpu().detach().numpy()==torch.argmax(y_train,dim=1).cpu().detach().numpy())
        count+=1
        losses=loss(pre,y_train)
        losses.backward()
        optim.step()
        print(corr,count)
        count=0
        print("train: ",corr/len(x_train))
        corr=0
        train_model.eval()
        test_pre=train_model(x_test)
        corr+=sum(torch.argmax(test_pre,dim=1).cpu().detach().numpy()==torch.argmax(y_test,dim=1).cpu().detach().numpy())
        print("validation dataet accuracy: ",corr/len(y_test))
train("D:/Living_and_Study_In_University/Dataset/UrbanSound8K")

8732it [00:02, 4074.99it/s]


(50, 173)
Number of training samples =  6985
Number of testing samples =  1747
200
400
Number of Parameters:  372150 0.05
torch.Size([6985, 173, 50]) torch.Size([6985, 10])
764 1
train:  0.10937723693629206
validation dataet accuracy:  0.13394390383514596
998 1
train:  0.14287759484609877
validation dataet accuracy:  0.1333714939896966
1016 1
train:  0.14545454545454545
validation dataet accuracy:  0.14367487120778477
1073 1
train:  0.15361488904795992
validation dataet accuracy:  0.159129937034917
1184 1
train:  0.1695060844667144
validation dataet accuracy:  0.1837435603892387
1344 1
train:  0.19241231209735146
validation dataet accuracy:  0.21007441327990842
1506 1
train:  0.21560486757337152
validation dataet accuracy:  0.22438465941614197
1574 1
train:  0.22534001431639228
validation dataet accuracy:  0.2169433314253005
1539 1
train:  0.2203292770221904
validation dataet accuracy:  0.20950200343445907
1466 1
train:  0.20987831066571225
validation dataet accuracy:  0.20778477389811

In [ ]:
#VIT 0.933
from torch.utils.data import DataLoader,Dataset
class UB8(Dataset):
    def __init__(self,path="D:/Living_and_Study_In_University/Dataset/UrbanSound8K",random_state=42,train=True):
        super(UB8,self).__init__()
        self.path=path
        self.random_state=random_state
        self.train=train
        self.df = pd.read_csv(self.path+'/metadata/UrbanSound8K.csv')
        extracted = []
        for index_num,row in tqdm(self.df.iterrows()):
            warnings.filterwarnings('ignore')
            file_name = os.path.join(os.path.abspath(self.path),'fold'+str(row["fold"])+'/',str(row['slice_file_name'])) 
            final_class_labels = row['class']   
            feature=np.load(os.path.abspath(self.path)+"/Numpy_4_gfcc_bfcc_mfcc_lfcc_ngcc/"+'fold'+str(row["fold"])+'/'+str(row['slice_file_name']).split('.')[0]+'.npy')
            extracted.append([feature,final_class_labels])
        ext_df = pd.DataFrame(extracted,columns=['feature','class'])
        x_all = np.array(ext_df[['feature']].to_numpy())
        x=[]
        for i in x_all:
            #print(i[0].shape)
            x.append(i[0])
        y = np.array(ext_df['class'].tolist())
        le = LabelEncoder()
        y = le.fit_transform(y)
        y_all=np.eye(10)[y]
        x_train, x_test, y_train, y_test = train_test_split(np.array(x), y_all, test_size=0.2, random_state = self.random_state)
        if self.train:
            self.x=torch.tensor(x_train).float()
            self.y=y_train
        else:
            self.x=torch.tensor(x_test).float()
            self.y=y_test
    def __getitem__(self,index):
        return self.x[index],self.y[index]
    def __len__(self):
        return len(self.x)
#Audio Single
from torch.utils.tensorboard import SummaryWriter
from timm.models.resnet import resnet50,resnet101
from timm.models.vision_transformer import VisionTransformer,vit_small_patch16_224
from timm.models.mobilenetv3 import MobileNetV3
model=vit_small_patch16_224(img_size=(399,100),in_chans=1,num_classes=10)
print(sum([i.nelement() for i in model.parameters()]))
train_dataset=UB8(train=True)
test_dataset=UB8(train=False)
batch_size=150
train_loader=DataLoader(train_dataset,batch_size=batch_size,shuffle=True)
test_loader=DataLoader(test_dataset,batch_size=batch_size,shuffle=True)
loss_function=nn.CrossEntropyLoss(label_smoothing=0.1)
optimizer=torch.optim.AdamW(model.parameters(),lr=0.001)
model.cuda()
model.train()
epoches=3500
wrtier=SummaryWriter("Classification")
count=0
for epoch in range(epoches):
    all_correct=0
    all_cnt=0
    train_loader=DataLoader(train_dataset,batch_size=batch_size,shuffle=True)
    test_loader=DataLoader(test_dataset,batch_size=batch_size,shuffle=True)
    model.train()
    for index,(data,label) in enumerate(train_loader):
        if(len(data.shape)==3):
            data=data.unsqueeze(1)
        if(count<=2):
            print(data.shape)
            count+=1
        data=data.cuda()
        label=label.cuda()
        optimizer.zero_grad()
        output=model(data)
        all_cnt+=data.shape[0]
        loss=loss_function(output,label)
        all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
        loss.backward()
        optimizer.step()
        #wrtier.add_scalar("Train_loss_Single_Modal",loss,index+epoch*len(train_loader))
        #wrtier.add_scalar("Train_accuracy_Single_Modal",all_correct/(all_cnt),index+epoch*len(train_loader))

    print("Epoch: ",epoch,"Train Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)
        
    model.eval()
    with torch.no_grad():
        all_correct=0
        all_cnt=0
        for index,(data,label) in enumerate(test_loader):
            if(len(data.shape)==3):
                data=data.unsqueeze(1)
            if(count<=2):
                print(data.shape)
                count+=1
            data=data.cuda()
            label=label.cuda()
            output=model(data)
            all_cnt+=data.shape[0]
            all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
            loss=loss_function(output,label)
            #wrtier.add_scalar("Test_accuracy_Single_Modal",all_correct/(all_cnt),epoch)
            #wrtier.add_scalar("Test_loss_Single_Modal",loss,epoch)
        print("Epoch: ",epoch,"Test Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)

In [ ]:
#mlp-mixer  0.947
from torch.utils.data import DataLoader,Dataset
class UB8(Dataset):
    def __init__(self,path="D:/Living_and_Study_In_University/Dataset/UrbanSound8K",random_state=42,train=True):
        super(UB8,self).__init__()
        self.path=path
        self.random_state=random_state
        self.train=train
        self.df = pd.read_csv(self.path+'/metadata/UrbanSound8K.csv')
        extracted = []
        for index_num,row in tqdm(self.df.iterrows()):
            warnings.filterwarnings('ignore')
            file_name = os.path.join(os.path.abspath(self.path),'fold'+str(row["fold"])+'/',str(row['slice_file_name'])) 
            final_class_labels = row['class']   
            feature=np.load(os.path.abspath(self.path)+"/Numpy_4_gfcc_bfcc_mfcc_lfcc_ngcc/"+'fold'+str(row["fold"])+'/'+str(row['slice_file_name']).split('.')[0]+'.npy')
            extracted.append([feature,final_class_labels])
        ext_df = pd.DataFrame(extracted,columns=['feature','class'])
        x_all = np.array(ext_df[['feature']].to_numpy())
        x=[]
        for i in x_all:
            #print(i[0].shape)
            x.append(i[0])
        y = np.array(ext_df['class'].tolist())
        le = LabelEncoder()
        y = le.fit_transform(y)
        y_all=np.eye(10)[y]
        x_train, x_test, y_train, y_test = train_test_split(np.array(x), y_all, test_size=0.2, random_state = self.random_state)
        if self.train:
            self.x=torch.tensor(x_train).float()
            self.y=y_train
        else:
            self.x=torch.tensor(x_test).float()
            self.y=y_test
    def __getitem__(self,index):
        return self.x[index],self.y[index]
    def __len__(self):
        return len(self.x)
#Audio Single
from torch.utils.tensorboard import SummaryWriter
from timm.models.resnet import resnet50,resnet101
from timm.models.vision_transformer import VisionTransformer,vit_small_patch16_224
from timm.models.mobilenetv3 import MobileNetV3
from timm.models.convnext import convnext_base
model=convnext_base(in_chans=1,num_classes=10)
print(sum([i.nelement() for i in model.parameters()]))
train_dataset=UB8(train=True)
test_dataset=UB8(train=False)
batch_size=100
train_loader=DataLoader(train_dataset,batch_size=batch_size,shuffle=True)
test_loader=DataLoader(test_dataset,batch_size=batch_size,shuffle=True)
loss_function=nn.CrossEntropyLoss(label_smoothing=0.1)
optimizer=torch.optim.AdamW(model.parameters(),lr=0.001)
model.cuda()
model.train()
epoches=3500
wrtier=SummaryWriter("Classification")
count=0
for epoch in range(epoches):
    all_correct=0
    all_cnt=0
    train_loader=DataLoader(train_dataset,batch_size=batch_size,shuffle=True)
    test_loader=DataLoader(test_dataset,batch_size=batch_size,shuffle=True)
    model.train()
    for index,(data,label) in enumerate(train_loader):
        if(len(data.shape)==3):
            data=data.unsqueeze(1)
        if(count<=2):
            print(data.shape)
            count+=1
        data=data.cuda()
        label=label.cuda()
        optimizer.zero_grad()
        output=model(data)
        all_cnt+=data.shape[0]
        loss=loss_function(output,label)
        all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
        loss.backward()
        optimizer.step()
        #wrtier.add_scalar("Train_loss_Single_Modal",loss,index+epoch*len(train_loader))
        #wrtier.add_scalar("Train_accuracy_Single_Modal",all_correct/(all_cnt),index+epoch*len(train_loader))

    print("Epoch: ",epoch,"Train Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)
        
    model.eval()
    with torch.no_grad():
        all_correct=0
        all_cnt=0
        for index,(data,label) in enumerate(test_loader):
            if(len(data.shape)==3):
                data=data.unsqueeze(1)
            if(count<=2):
                print(data.shape)
                count+=1
            data=data.cuda()
            label=label.cuda()
            output=model(data)
            all_cnt+=data.shape[0]
            all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
            loss=loss_function(output,label)
            #wrtier.add_scalar("Test_accuracy_Single_Modal",all_correct/(all_cnt),epoch)
            #wrtier.add_scalar("Test_loss_Single_Modal",loss,epoch)
        print("Epoch: ",epoch,"Test Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)

In [ ]:
#Coat Tiny 94.4
from torch.utils.data import DataLoader,Dataset
class UB8(Dataset):
    def __init__(self,path="D:/Living_and_Study_In_University/Dataset/UrbanSound8K",random_state=42,train=True):
        super(UB8,self).__init__()
        self.path=path
        self.random_state=random_state
        self.train=train
        self.df = pd.read_csv(self.path+'/metadata/UrbanSound8K.csv')
        extracted = []
        for index_num,row in tqdm(self.df.iterrows()):
            warnings.filterwarnings('ignore')
            file_name = os.path.join(os.path.abspath(self.path),'fold'+str(row["fold"])+'/',str(row['slice_file_name'])) 
            final_class_labels = row['class']   
            feature=np.load(os.path.abspath(self.path)+"/Numpy_4_gfcc_bfcc_mfcc_lfcc_ngcc/"+'fold'+str(row["fold"])+'/'+str(row['slice_file_name']).split('.')[0]+'.npy')
            extracted.append([feature,final_class_labels])
        ext_df = pd.DataFrame(extracted,columns=['feature','class'])
        x_all = np.array(ext_df[['feature']].to_numpy())
        x=[]
        for i in x_all:
            #print(i[0].shape)
            x.append(i[0])
        y = np.array(ext_df['class'].tolist())
        le = LabelEncoder()
        y = le.fit_transform(y)
        y_all=np.eye(10)[y]
        x_train, x_test, y_train, y_test = train_test_split(np.array(x), y_all, test_size=0.2, random_state = self.random_state)
        if self.train:
            self.x=torch.tensor(x_train).float()
            self.y=y_train
        else:
            self.x=torch.tensor(x_test).float()
            self.y=y_test
    def __getitem__(self,index):
        return self.x[index],self.y[index]
    def __len__(self):
        return len(self.x)
#Audio Single
from torch.utils.tensorboard import SummaryWriter
from timm.models.resnet import resnet50,resnet101,resnet200
from timm.models.vision_transformer import VisionTransformer,vit_small_patch16_224
from timm.models.mobilenetv3 import MobileNetV3
from timm.models.convnext import convnext_base
from timm.models.mlp_mixer import MlpMixer
from timm.models.swin_transformer import swin_base_patch4_window7_224
from timm.models.coat import coat_lite_mini,CoaT
CoaT()
model=coat_lite_mini(in_chans=1,num_classes=10,img_size=(399,100))
print(sum([i.nelement() for i in model.parameters()]))
train_dataset=UB8(train=True)
test_dataset=UB8(train=False)
batch_size=100
train_loader=DataLoader(train_dataset,batch_size=batch_size,shuffle=True)
test_loader=DataLoader(test_dataset,batch_size=batch_size,shuffle=True)
loss_function=nn.CrossEntropyLoss(label_smoothing=0.1)
optimizer=torch.optim.AdamW(model.parameters(),lr=0.001)
model.cuda()
model.train()
epoches=3500
wrtier=SummaryWriter("Classification")
count=0
for epoch in range(epoches):
    all_correct=0
    all_cnt=0
    train_loader=DataLoader(train_dataset,batch_size=batch_size,shuffle=True)
    test_loader=DataLoader(test_dataset,batch_size=batch_size,shuffle=True)
    model.train()
    for index,(data,label) in enumerate(train_loader):
        if(len(data.shape)==3):
            data=data.unsqueeze(1)
        if(count<=2):
            print(data.shape)
            count+=1
        data=data.cuda()
        label=label.cuda()
        optimizer.zero_grad()
        output=model(data)
        all_cnt+=data.shape[0]
        loss=loss_function(output,label)
        all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
        loss.backward()
        optimizer.step()
        #wrtier.add_scalar("Train_loss_Single_Modal",loss,index+epoch*len(train_loader))
        #wrtier.add_scalar("Train_accuracy_Single_Modal",all_correct/(all_cnt),index+epoch*len(train_loader))

    print("Epoch: ",epoch,"Train Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)
        
    model.eval()
    with torch.no_grad():
        all_correct=0
        all_cnt=0
        for index,(data,label) in enumerate(test_loader):
            if(len(data.shape)==3):
                data=data.unsqueeze(1)
            if(count<=2):
                print(data.shape)
                count+=1
            data=data.cuda()
            label=label.cuda()
            output=model(data)
            all_cnt+=data.shape[0]
            all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
            loss=loss_function(output,label)
            #wrtier.add_scalar("Test_accuracy_Single_Modal",all_correct/(all_cnt),epoch)
            #wrtier.add_scalar("Test_loss_Single_Modal",loss,epoch)
        print("Epoch: ",epoch,"Test Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)

In [ ]:
#Coat middle 92.5
from torch.utils.data import DataLoader,Dataset
class UB8(Dataset):
    def __init__(self,path="D:/Living_and_Study_In_University/Dataset/UrbanSound8K",random_state=42,train=True):
        super(UB8,self).__init__()
        self.path=path
        self.random_state=random_state
        self.train=train
        self.df = pd.read_csv(self.path+'/metadata/UrbanSound8K.csv')
        extracted = []
        for index_num,row in tqdm(self.df.iterrows()):
            warnings.filterwarnings('ignore')
            file_name = os.path.join(os.path.abspath(self.path),'fold'+str(row["fold"])+'/',str(row['slice_file_name'])) 
            final_class_labels = row['class']   
            feature=np.load(os.path.abspath(self.path)+"/Numpy_4_gfcc_bfcc_mfcc_lfcc_ngcc/"+'fold'+str(row["fold"])+'/'+str(row['slice_file_name']).split('.')[0]+'.npy')
            extracted.append([feature,final_class_labels])
        ext_df = pd.DataFrame(extracted,columns=['feature','class'])
        x_all = np.array(ext_df[['feature']].to_numpy())
        x=[]
        for i in x_all:
            #print(i[0].shape)
            x.append(i[0])
        y = np.array(ext_df['class'].tolist())
        le = LabelEncoder()
        y = le.fit_transform(y)
        y_all=np.eye(10)[y]
        x_train, x_test, y_train, y_test = train_test_split(np.array(x), y_all, test_size=0.2, random_state = self.random_state)
        if self.train:
            self.x=torch.tensor(x_train).float()
            self.y=y_train
        else:
            self.x=torch.tensor(x_test).float()
            self.y=y_test
    def __getitem__(self,index):
        return self.x[index],self.y[index]
    def __len__(self):
        return len(self.x)
#Audio Single
from torch.utils.tensorboard import SummaryWriter
from timm.models.resnet import resnet50,resnet101,resnet200
from timm.models.vision_transformer import VisionTransformer,vit_small_patch16_224
from timm.models.mobilenetv3 import MobileNetV3
from timm.models.convnext import convnext_base
from timm.models.mlp_mixer import MlpMixer
from timm.models.swin_transformer import swin_base_patch4_window7_224
from timm.models.coat import coat_lite_small,coat_lite_mini,coat_tiny
from timm.models.coat import coat_tiny
model=coat_lite_small(in_chans=1,num_classes=10,img_size=(399,100))
print(sum([i.nelement() for i in model.parameters()]))
train_dataset=UB8(train=True)
test_dataset=UB8(train=False)
batch_size=100
train_loader=DataLoader(train_dataset,batch_size=batch_size,shuffle=True)
test_loader=DataLoader(test_dataset,batch_size=batch_size,shuffle=True)
loss_function=nn.CrossEntropyLoss(label_smoothing=0.1)
optimizer=torch.optim.AdamW(model.parameters(),lr=0.001)
model.cuda()
model.train()
epoches=3500
wrtier=SummaryWriter("Classification")
count=0
for epoch in range(epoches):
    all_correct=0
    all_cnt=0
    train_loader=DataLoader(train_dataset,batch_size=batch_size,shuffle=True)
    test_loader=DataLoader(test_dataset,batch_size=batch_size,shuffle=True)
    model.train()
    for index,(data,label) in enumerate(train_loader):
        if(len(data.shape)==3):
            data=data.unsqueeze(1)
        if(count<=2):
            print(data.shape)
            count+=1
        data=data.cuda()
        label=label.cuda()
        optimizer.zero_grad()
        output=model(data)
        all_cnt+=data.shape[0]
        loss=loss_function(output,label)
        all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
        loss.backward()
        optimizer.step()
        #wrtier.add_scalar("Train_loss_Single_Modal",loss,index+epoch*len(train_loader))
        #wrtier.add_scalar("Train_accuracy_Single_Modal",all_correct/(all_cnt),index+epoch*len(train_loader))

    print("Epoch: ",epoch,"Train Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)
        
    model.eval()
    with torch.no_grad():
        all_correct=0
        all_cnt=0
        for index,(data,label) in enumerate(test_loader):
            if(len(data.shape)==3):
                data=data.unsqueeze(1)
            if(count<=2):
                print(data.shape)
                count+=1
            data=data.cuda()
            label=label.cuda()
            output=model(data)
            all_cnt+=data.shape[0]
            all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
            loss=loss_function(output,label)
            #wrtier.add_scalar("Test_accuracy_Single_Modal",all_correct/(all_cnt),epoch)
            #wrtier.add_scalar("Test_loss_Single_Modal",loss,epoch)
        print("Epoch: ",epoch,"Test Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)

In [ ]:
#Covnext  94.7
from torch.utils.data import DataLoader,Dataset
class UB8(Dataset):
    def __init__(self,path="D:/Living_and_Study_In_University/Dataset/UrbanSound8K",random_state=42,train=True):
        super(UB8,self).__init__()
        self.path=path
        self.random_state=random_state
        self.train=train
        self.df = pd.read_csv(self.path+'/metadata/UrbanSound8K.csv')
        extracted = []
        for index_num,row in tqdm(self.df.iterrows()):
            warnings.filterwarnings('ignore')
            file_name = os.path.join(os.path.abspath(self.path),'fold'+str(row["fold"])+'/',str(row['slice_file_name'])) 
            final_class_labels = row['class']   
            feature=np.load(os.path.abspath(self.path)+"/Numpy_4_gfcc_bfcc_mfcc_lfcc_ngcc/"+'fold'+str(row["fold"])+'/'+str(row['slice_file_name']).split('.')[0]+'.npy')
            extracted.append([feature,final_class_labels])
        ext_df = pd.DataFrame(extracted,columns=['feature','class'])
        x_all = np.array(ext_df[['feature']].to_numpy())
        x=[]
        for i in x_all:
            #print(i[0].shape)
            x.append(i[0])
        y = np.array(ext_df['class'].tolist())
        le = LabelEncoder()
        y = le.fit_transform(y)
        y_all=np.eye(10)[y]
        x_train, x_test, y_train, y_test = train_test_split(np.array(x), y_all, test_size=0.2, random_state = self.random_state)
        if self.train:
            self.x=torch.tensor(x_train).float()
            self.y=y_train
        else:
            self.x=torch.tensor(x_test).float()
            self.y=y_test
    def __getitem__(self,index):
        return self.x[index],self.y[index]
    def __len__(self):
        return len(self.x)
#Audio Single
from torch.utils.tensorboard import SummaryWriter
from timm.models.resnet import resnet50,resnet101,resnet200
from timm.models.vision_transformer import VisionTransformer,vit_small_patch16_224
from timm.models.mobilenetv3 import MobileNetV3
from timm.models.convnext import convnext_base
from timm.models.mlp_mixer import MlpMixer
from timm.models.swin_transformer import swin_base_patch4_window7_224
from timm.models.coat import coat_lite_small,coat_lite_mini,coat_tiny
from timm.models.coat import coat_tiny
from timm.models.convnext import convnext_base
model=convnext_base(in_chans=1,num_classes=10)
print(sum([i.nelement() for i in model.parameters()]))
train_dataset=UB8(train=True)
test_dataset=UB8(train=False)
batch_size=100
train_loader=DataLoader(train_dataset,batch_size=batch_size,shuffle=True)
test_loader=DataLoader(test_dataset,batch_size=batch_size,shuffle=True)
loss_function=nn.CrossEntropyLoss(label_smoothing=0.1)
optimizer=torch.optim.AdamW(model.parameters(),lr=0.001)
model.cuda()
model.train()
epoches=3500
wrtier=SummaryWriter("Classification")
count=0
for epoch in range(epoches):
    all_correct=0
    all_cnt=0
    train_loader=DataLoader(train_dataset,batch_size=batch_size,shuffle=True)
    test_loader=DataLoader(test_dataset,batch_size=batch_size,shuffle=True)
    model.train()
    for index,(data,label) in enumerate(train_loader):
        if(len(data.shape)==3):
            data=data.unsqueeze(1)
        if(count<=2):
            print(data.shape)
            count+=1
        data=data.cuda()
        label=label.cuda()
        optimizer.zero_grad()
        output=model(data)
        all_cnt+=data.shape[0]
        loss=loss_function(output,label)
        all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
        loss.backward()
        optimizer.step()
        #wrtier.add_scalar("Train_loss_Single_Modal",loss,index+epoch*len(train_loader))
        #wrtier.add_scalar("Train_accuracy_Single_Modal",all_correct/(all_cnt),index+epoch*len(train_loader))

    print("Epoch: ",epoch,"Train Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)
        
    model.eval()
    with torch.no_grad():
        all_correct=0
        all_cnt=0
        for index,(data,label) in enumerate(test_loader):
            if(len(data.shape)==3):
                data=data.unsqueeze(1)
            if(count<=2):
                print(data.shape)
                count+=1
            data=data.cuda()
            label=label.cuda()
            output=model(data)
            all_cnt+=data.shape[0]
            all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
            loss=loss_function(output,label)
            #wrtier.add_scalar("Test_accuracy_Single_Modal",all_correct/(all_cnt),epoch)
            #wrtier.add_scalar("Test_loss_Single_Modal",loss,epoch)
        print("Epoch: ",epoch,"Test Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)

In [ ]:
#convit_small  0.95
from torch.utils.data import DataLoader,Dataset
class UB8(Dataset):
    def __init__(self,path="D:/Living_and_Study_In_University/Dataset/UrbanSound8K",random_state=42,train=True):
        super(UB8,self).__init__()
        self.path=path
        self.random_state=random_state
        self.train=train
        self.df = pd.read_csv(self.path+'/metadata/UrbanSound8K.csv')
        extracted = []
        for index_num,row in tqdm(self.df.iterrows()):
            warnings.filterwarnings('ignore')
            file_name = os.path.join(os.path.abspath(self.path),'fold'+str(row["fold"])+'/',str(row['slice_file_name'])) 
            final_class_labels = row['class']   
            feature=np.load(os.path.abspath(self.path)+"/Numpy_4_gfcc_bfcc_mfcc_lfcc_ngcc/"+'fold'+str(row["fold"])+'/'+str(row['slice_file_name']).split('.')[0]+'.npy')
            extracted.append([feature,final_class_labels])
        ext_df = pd.DataFrame(extracted,columns=['feature','class'])
        x_all = np.array(ext_df[['feature']].to_numpy())
        x=[]
        for i in x_all:
            #print(i[0].shape)
            x.append(i[0])
        y = np.array(ext_df['class'].tolist())
        le = LabelEncoder()
        y = le.fit_transform(y)
        y_all=np.eye(10)[y]
        x_train, x_test, y_train, y_test = train_test_split(np.array(x), y_all, test_size=0.2, random_state = self.random_state)
        if self.train:
            self.x=torch.tensor(x_train).float()
            self.y=y_train
        else:
            self.x=torch.tensor(x_test).float()
            self.y=y_test
    def __getitem__(self,index):
        return self.x[index],self.y[index]
    def __len__(self):
        return len(self.x)
#Audio Single
from torch.utils.tensorboard import SummaryWriter
from timm.models.resnet import resnet50,resnet101,resnet200
from timm.models.vision_transformer import VisionTransformer,vit_small_patch16_224
from timm.models.mobilenetv3 import MobileNetV3
from timm.models.convnext import convnext_base
from timm.models.mlp_mixer import MlpMixer
from timm.models.swin_transformer import swin_base_patch4_window7_224
from timm.models.coat import coat_lite_small,coat_lite_mini,coat_tiny
from timm.models.coat import coat_tiny
from timm.models.convnext import convnext_base
from timm.models.convit import convit_base, ConViT,convit_tiny,convit_small

model=convit_small(in_chans=1,num_classes=10,img_size=(399,100))
print(sum([i.nelement() for i in model.parameters()]))
train_dataset=UB8(train=True)
test_dataset=UB8(train=False)
batch_size=100
train_loader=DataLoader(train_dataset,batch_size=batch_size,shuffle=True)
test_loader=DataLoader(test_dataset,batch_size=batch_size,shuffle=True)
loss_function=nn.CrossEntropyLoss(label_smoothing=0.1)
optimizer=torch.optim.AdamW(model.parameters(),lr=0.001)
model.cuda()
model.train()
epoches=3500
wrtier=SummaryWriter("Classification")
count=0
for epoch in range(epoches):
    all_correct=0
    all_cnt=0
    train_loader=DataLoader(train_dataset,batch_size=batch_size,shuffle=True)
    test_loader=DataLoader(test_dataset,batch_size=batch_size,shuffle=True)
    model.train()
    for index,(data,label) in enumerate(train_loader):
        if(len(data.shape)==3):
            data=data.unsqueeze(1)
        if(count<=2):
            print(data.shape)
            count+=1
        data=data.cuda()
        label=label.cuda()
        optimizer.zero_grad()
        output=model(data)
        all_cnt+=data.shape[0]
        loss=loss_function(output,label)
        all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
        loss.backward()
        optimizer.step()
        #wrtier.add_scalar("Train_loss_Single_Modal",loss,index+epoch*len(train_loader))
        #wrtier.add_scalar("Train_accuracy_Single_Modal",all_correct/(all_cnt),index+epoch*len(train_loader))

    print("Epoch: ",epoch,"Train Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)
        
    model.eval()
    with torch.no_grad():
        all_correct=0
        all_cnt=0
        for index,(data,label) in enumerate(test_loader):
            if(len(data.shape)==3):
                data=data.unsqueeze(1)
            if(count<=2):
                print(data.shape)
                count+=1
            data=data.cuda()
            label=label.cuda()
            output=model(data)
            all_cnt+=data.shape[0]
            all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
            loss=loss_function(output,label)
            #wrtier.add_scalar("Test_accuracy_Single_Modal",all_correct/(all_cnt),epoch)
            #wrtier.add_scalar("Test_loss_Single_Modal",loss,epoch)
        print("Epoch: ",epoch,"Test Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)

In [ ]:
#convit_tiny 0.935
from torch.utils.data import DataLoader,Dataset
class UB8(Dataset):
    def __init__(self,path="D:/Living_and_Study_In_University/Dataset/UrbanSound8K",random_state=42,train=True):
        super(UB8,self).__init__()
        self.path=path
        self.random_state=random_state
        self.train=train
        self.df = pd.read_csv(self.path+'/metadata/UrbanSound8K.csv')
        extracted = []
        for index_num,row in tqdm(self.df.iterrows()):
            warnings.filterwarnings('ignore')
            file_name = os.path.join(os.path.abspath(self.path),'fold'+str(row["fold"])+'/',str(row['slice_file_name'])) 
            final_class_labels = row['class']   
            feature=np.load(os.path.abspath(self.path)+"/Numpy_4_gfcc_bfcc_mfcc_lfcc_ngcc/"+'fold'+str(row["fold"])+'/'+str(row['slice_file_name']).split('.')[0]+'.npy')
            extracted.append([feature,final_class_labels])
        ext_df = pd.DataFrame(extracted,columns=['feature','class'])
        x_all = np.array(ext_df[['feature']].to_numpy())
        x=[]
        for i in x_all:
            #print(i[0].shape)
            x.append(i[0])
        y = np.array(ext_df['class'].tolist())
        le = LabelEncoder()
        y = le.fit_transform(y)
        y_all=np.eye(10)[y]
        x_train, x_test, y_train, y_test = train_test_split(np.array(x), y_all, test_size=0.2, random_state = self.random_state)
        if self.train:
            self.x=torch.tensor(x_train).float()
            self.y=y_train
        else:
            self.x=torch.tensor(x_test).float()
            self.y=y_test
    def __getitem__(self,index):
        return self.x[index],self.y[index]
    def __len__(self):
        return len(self.x)
#Audio Single
from torch.utils.tensorboard import SummaryWriter
from timm.models.resnet import resnet50,resnet101,resnet200
from timm.models.vision_transformer import VisionTransformer,vit_small_patch16_224
from timm.models.mobilenetv3 import MobileNetV3
from timm.models.convnext import convnext_base
from timm.models.mlp_mixer import MlpMixer
from timm.models.swin_transformer import swin_base_patch4_window7_224
from timm.models.coat import coat_lite_small,coat_lite_mini,coat_tiny
from timm.models.coat import coat_tiny
from timm.models.convnext import convnext_base
from timm.models.convit import convit_base, ConViT,convit_tiny,convit_small

model=convit_tiny(in_chans=1,num_classes=10,img_size=(399,100))
print(sum([i.nelement() for i in model.parameters()]))
train_dataset=UB8(train=True)
test_dataset=UB8(train=False)
batch_size=100
train_loader=DataLoader(train_dataset,batch_size=batch_size,shuffle=True)
test_loader=DataLoader(test_dataset,batch_size=batch_size,shuffle=True)
loss_function=nn.CrossEntropyLoss(label_smoothing=0.1)
optimizer=torch.optim.AdamW(model.parameters(),lr=0.001)
model.cuda()
model.train()
epoches=3500
wrtier=SummaryWriter("Classification")
count=0
for epoch in range(epoches):
    all_correct=0
    all_cnt=0
    train_loader=DataLoader(train_dataset,batch_size=batch_size,shuffle=True)
    test_loader=DataLoader(test_dataset,batch_size=batch_size,shuffle=True)
    model.train()
    for index,(data,label) in enumerate(train_loader):
        if(len(data.shape)==3):
            data=data.unsqueeze(1)
        if(count<=2):
            print(data.shape)
            count+=1
        data=data.cuda()
        label=label.cuda()
        optimizer.zero_grad()
        output=model(data)
        all_cnt+=data.shape[0]
        loss=loss_function(output,label)
        all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
        loss.backward()
        optimizer.step()
        #wrtier.add_scalar("Train_loss_Single_Modal",loss,index+epoch*len(train_loader))
        #wrtier.add_scalar("Train_accuracy_Single_Modal",all_correct/(all_cnt),index+epoch*len(train_loader))

    print("Epoch: ",epoch,"Train Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)
        
    model.eval()
    with torch.no_grad():
        all_correct=0
        all_cnt=0
        for index,(data,label) in enumerate(test_loader):
            if(len(data.shape)==3):
                data=data.unsqueeze(1)
            if(count<=2):
                print(data.shape)
                count+=1
            data=data.cuda()
            label=label.cuda()
            output=model(data)
            all_cnt+=data.shape[0]
            all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
            loss=loss_function(output,label)
            #wrtier.add_scalar("Test_accuracy_Single_Modal",all_correct/(all_cnt),epoch)
            #wrtier.add_scalar("Test_loss_Single_Modal",loss,epoch)
        print("Epoch: ",epoch,"Test Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)

In [ ]:
# DeitIII
from torch.utils.data import DataLoader,Dataset
class UB8(Dataset):
    def __init__(self,path="D:/Living_and_Study_In_University/Dataset/UrbanSound8K",random_state=42,train=True):
        super(UB8,self).__init__()
        self.path=path
        self.random_state=random_state
        self.train=train
        self.df = pd.read_csv(self.path+'/metadata/UrbanSound8K.csv')
        extracted = []
        for index_num,row in tqdm(self.df.iterrows()):
            warnings.filterwarnings('ignore')
            file_name = os.path.join(os.path.abspath(self.path),'fold'+str(row["fold"])+'/',str(row['slice_file_name'])) 
            final_class_labels = row['class']   
            feature=np.load(os.path.abspath(self.path)+"/Numpy_4_gfcc_bfcc_mfcc_lfcc_ngcc/"+'fold'+str(row["fold"])+'/'+str(row['slice_file_name']).split('.')[0]+'.npy')
            extracted.append([feature,final_class_labels])
        ext_df = pd.DataFrame(extracted,columns=['feature','class'])
        x_all = np.array(ext_df[['feature']].to_numpy())
        x=[]
        for i in x_all:
            #print(i[0].shape)
            x.append(i[0])
        y = np.array(ext_df['class'].tolist())
        le = LabelEncoder()
        y = le.fit_transform(y)
        y_all=np.eye(10)[y]
        x_train, x_test, y_train, y_test = train_test_split(np.array(x), y_all, test_size=0.2, random_state = self.random_state)
        if self.train:
            self.x=torch.tensor(x_train).float()
            self.y=y_train
        else:
            self.x=torch.tensor(x_test).float()
            self.y=y_test
    def __getitem__(self,index):
        return self.x[index],self.y[index]
    def __len__(self):
        return len(self.x)
#Audio Single
from torch.utils.tensorboard import SummaryWriter
from timm.models.resnet import resnet50,resnet101,resnet200
from timm.models.vision_transformer import VisionTransformer,vit_small_patch16_224
from timm.models.mobilenetv3 import MobileNetV3
from timm.models.convnext import convnext_base
from timm.models.mlp_mixer import MlpMixer
from timm.models.swin_transformer import swin_base_patch4_window7_224
from timm.models.coat import coat_lite_small,coat_lite_mini,coat_tiny
from timm.models.coat import coat_tiny
from timm.models.convnext import convnext_base
from timm.models.convit import convit_base, ConViT,convit_tiny,convit_small
from timm.models.deit import deit3_base_patch16_224,deit3_small_patch16_224
from timm.models.mobilevit import   mobilevitv2_200
from tqdm.notebook import tqdm_notebook
#model=mobilevitv2_200(in_chans=1,num_classes=10,img_size=(399,100))
print(sum([i.nelement() for i in model.parameters()]))
train_dataset=UB8(train=True)
test_dataset=UB8(train=False)
batch_size=100
train_loader=DataLoader(train_dataset,batch_size=batch_size,shuffle=True)
test_loader=DataLoader(test_dataset,batch_size=batch_size,shuffle=True)
loss_function=nn.CrossEntropyLoss(label_smoothing=0.1)
optimizer=torch.optim.AdamW(model.parameters(),lr=0.001)
model.cuda()
model.train()
epoches=3500
wrtier=SummaryWriter("Classification")
count=0
for epoch in range(epoches):
    all_correct=0
    all_cnt=0
    train_loader=DataLoader(train_dataset,batch_size=batch_size,shuffle=True)
    test_loader=DataLoader(test_dataset,batch_size=batch_size,shuffle=True)
    model.train()
    for index,(data,label) in enumerate(train_loader):
        if(len(data.shape)==3):
            data=data.unsqueeze(1)
        if(count<=2):
            print(data.shape)
            count+=1
        data=data.cuda()
        label=label.cuda()
        optimizer.zero_grad()
        output=model(data)
        all_cnt+=data.shape[0]
        loss=loss_function(output,label)
        all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
        loss.backward()
        optimizer.step()
        #wrtier.add_scalar("Train_loss_Single_Modal",loss,index+epoch*len(train_loader))
        #wrtier.add_scalar("Train_accuracy_Single_Modal",all_correct/(all_cnt),index+epoch*len(train_loader))

    print("Epoch: ",epoch,"Train Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)
        
    model.eval()
    with torch.no_grad():
        all_correct=0
        all_cnt=0
        for index,(data,label) in enumerate(test_loader):
            if(len(data.shape)==3):
                data=data.unsqueeze(1)
            if(count<=2):
                print(data.shape)
                count+=1
            data=data.cuda()
            label=label.cuda()
            output=model(data)
            all_cnt+=data.shape[0]
            all_correct+=torch.sum(torch.argmax(output,dim=1)==torch.argmax(label,dim=1))
            loss=loss_function(output,label)
            #wrtier.add_scalar("Test_accuracy_Single_Modal",all_correct/(all_cnt),epoch)
            #wrtier.add_scalar("Test_loss_Single_Modal",loss,epoch)
        print("Epoch: ",epoch,"Test Accuracy: ",all_correct/(all_cnt)," Loss: ",loss)